In [1]:
import pickle
import numpy as np
import pandas as pd
import statistics
from os import listdir
import pycaret
from pycaret.classification import *
from sklearn.decomposition import PCA
from imblearn.over_sampling import SMOTE
from datetime import datetime
from sklearn.model_selection import train_test_split
from sklearn import preprocessing

# WESAD

In [3]:
wesad_dataset = pd.read_csv('Final_CSVs/wesad_id.csv')

In [4]:
wesad_dataset

id        EDA_0        EDA_1        EDA_2        EDA_3        TEMP_0  \
0       2  5452.450365  5366.846848  5264.122627  5115.746165  10279.722091   
1       2  5264.122627  5115.746165  5127.156998  5013.021944  10279.722091   
2       2  5127.156998  5013.021944  5372.556718  5235.591090  10279.722091   
3       2  5372.556718  5235.591090  5184.228979  5155.692989  10279.722091   
4       2  5184.228979  5155.692989  5115.746165  5081.504758  10464.748540   
...    ..          ...          ...          ...          ...           ...   
78761  17 -1141.515991 -1141.515991 -1146.439053 -1141.515991 -11412.917628   
78762  17 -1146.439053 -1141.515991 -1141.515991 -1141.515991 -11802.683112   
78763  17 -1141.515991 -1141.515991 -1136.589079 -1151.365964 -11802.683112   
78764  17 -1136.589079 -1151.365964 -1141.515991 -1141.515991 -11802.683112   
78765  17 -1141.515991 -1141.515991 -1136.589079 -1151.365964 -11802.683112   

             TEMP_1        TEMP_2        TEMP_3      ACC1_0      ACC1_1  \
0      10279.722091  10279.722091  10279.722091  126.326243  233.101284   
1      10279.722091  10279.722091  10279.722091   90.734562   78.870669   
2      10279.722091  10279.722091  10279.722091  -27.904372  -63.496052   
3      10279.722091  10464.748540  10464.748540  -27.904372  -27.904372   
4      10464.748540  10464.748540  10464.748540  -39.768266  -39.768266   
...             ...           ...           ...         ...         ...   
78761 -11802.683112 -11802.683112 -11802.683112   57.652528   57.652528   
78762 -11802.683112 -11802.683112 -11802.683112   57.652528   57.652528   
78763 -11802.683112 -11802.683112 -11802.683112   57.652528   57.652528   
78764 -11802.683112 -11802.683112 -11412.917628   57.652528   57.652528   
78765 -11412.917628 -11412.917628 -11412.917628   57.652528   57.652528   

           ACC1_2      ACC1_3      ACC1_4      ACC1_5      ACC1_6      ACC1_7  \
0      411.059685  304.284644  150.054030  161.917923   78.870669   67.006775   
1      114.462349  126.326243   55.142882   78.870669  161.917923  126.326243   
2      -27.904372   19.551202   43.278989   31.415095   19.551202  -27.904372   
3      -27.904372  -27.904372  -39.768266  -27.904372  -27.904372  -39.768266   
4      -27.904372  -39.768266  -27.904372  -39.768266  -27.904372  -27.904372   
...           ...         ...         ...         ...         ...         ...   
78761   57.652528   57.652528   57.652528   57.652528   57.652528   57.652528   
78762   57.652528   40.555758   57.652528   57.652528   57.652528   57.652528   
78763   57.652528   57.652528   57.652528   57.652528   57.652528   57.652528   
78764   57.652528   40.555758   57.652528   57.652528   57.652528   57.652528   
78765   57.652528   57.652528   57.652528   57.652528   57.652528   57.652528   

           ACC1_8      ACC1_9     ACC1_10    ACC1_11     ACC1_12     ACC1_13  \
0       55.142882  102.598456  102.598456  90.734562   90.734562   90.734562   
1      161.917923   31.415095    7.687308  90.734562  138.190136  138.190136   
2      -39.768266  -51.632159  -27.904372 -39.768266  -16.040479  -16.040479   
3      -27.904372  -27.904372  -39.768266 -27.904372  -27.904372  -27.904372   
4      -39.768266  -39.768266  -27.904372 -39.768266  -39.768266  -27.904372   
...           ...         ...         ...        ...         ...         ...   
78761   57.652528   57.652528   57.652528  57.652528   57.652528   57.652528   
78762   57.652528   57.652528   57.652528  57.652528   57.652528   57.652528   
78763   57.652528   57.652528   57.652528  57.652528   57.652528   57.652528   
78764   57.652528   57.652528   57.652528  57.652528   57.652528   57.652528   
78765   57.652528   57.652528   57.652528  57.652528   57.652528   57.652528   

          ACC1_14    ACC1_15    ACC1_16    ACC1_17     ACC1_18     ACC1_19  \
0      102.598456  90.734562  90.734562  78.870669  114.462349  126.326243   
1       78.870669  67.006775 -27.904372 -63.496052  -27.904372   19

In [5]:
for col in wesad_dataset.columns:
    new_col = col.replace("_","1")
    wesad_dataset = wesad_dataset.rename(columns={col: new_col})

In [6]:
# Train-Validation-Test Split for Deep Learning Implementation

X = wesad_dataset[wesad_dataset.columns.difference(['stress'])]
y = wesad_dataset["stress"]

X_train1, X_test, y_train1, y_test = train_test_split(X, y, test_size=0.25, random_state=123)
X_train, X_val, y_train, y_val = train_test_split(X_train1, y_train1, test_size=0.15, random_state=123)

X_train["dataset"] = 'Train'
X_val["dataset"] = 'Val'
X_test["dataset"] = 'Test'

In [7]:
X_train

ACC110      ACC111     ACC1110     ACC1111     ACC1112     ACC1113  \
49519  275.095822  257.706505  309.874457  335.958433  309.874457  214.233212   
10257 -627.837227 -680.813133 -866.228804 -707.301086 -548.373367 -548.373367   
12034 -495.397461 -495.397461 -495.397461 -521.885414 -495.397461 -495.397461   
2349  -312.637815 -336.365602 -348.229495 -360.093388 -300.773921 -336.365602   
64334   -7.235882   -7.235882   -7.235882   -7.235882   -7.235882   -7.235882   
...           ...         ...         ...         ...         ...         ...   
29110   -1.922477   -1.922477   -1.922477   -7.482866   -1.922477   -7.482866   
70152  247.459664  286.805828  286.805828  326.151992  326.151992  326.151992   
29087   -7.482866   14.758692  -13.043256  -68.647152   -7.482866  -18.603645   
67936   55.135647   55.135647   55.135647   46.225429   46.225429   55.135647   
36047   55.332661   55.332661   55.332661   55.332661   55.332661   55.332661   

          ACC1114     ACC1115     ACC1116     ACC1117     ACC1118     ACC1119  \
49519  257.706505  344.653091  370.737067  335.958433  318.569115  301.179798   
10257 -521.885414 -574.861320 -601.349274 -627.837227 -654.325180 -627.837227   
12034 -495.397461 -495.397461 -495.397461 -495.397461 -495.397461 -495.397461   
2349  -348.229495 -348.229495 -383.821175 -371.957282 -360.093388 -371.957282   
64334   -7.235882   -7.235882   -7.235882   -7.235882   -7.235882   -7.235882   
...           ...         ...         ...         ...         ...         ...   
29110   -7.482866   -7.482866   -1.922477   -7.482866  -13.043256  -13.043256   
70152  286.805828  326.151992  365.498156  365.498156  326.151992  286.805828   
29087   -7.482866   -1.922477   -7.482866   -7.482866   -1.922477   -1.922477   
67936   55.135647   55.135647   46.225429   55.135647   55.135647   55.135647   
36047   55.332661   55.332661   55.332661   55.332661   55.332661   55.332661   

           ACC112     ACC1120     ACC1121     ACC1122     ACC1123     ACC1124  \
49519  249.011847  266.401164  266.401164  266.401164  309.874457  327.263774   
10257 -707.301086 -627.837227 -627.837227 -627.837227 -627.837227 -627.837227   
12034 -495.397461 -495.397461 -495.397461 -495.397461 -495.397461 -495.397461   
2349  -348.229495 -383.821175 -371.957282 -383.821175 -348.229495 -360.093388   
64334   -7.235882   -7.235882   -7.235882   -7.235882   -7.235882   -7.235882   
...           ...         ...         ...         ...         ...         ...   
29110   -1.922477   -1.922477  -13.043256   -1.922477    3.637913   -7.482866   
70152  247.459664  326.151992  365.498156  365.498156  365.498156  365.498156   
29087    3.637913  -18.603645  -13.043256  -13.043256  -13.043256  -13.043256   
67936   55.135647   55.135647   55.135647   55.135647   46.225429   55.135647   
36047   62.664237   55.332661   55.332661   55.332661   55.332661   55.332661   

          ACC1125     ACC1126     ACC1127     ACC1128     ACC1129      ACC113  \
49519  335.958433  283.790481  301.179798  266.401164  196.843895  266.401164   
10257 -654.325180 -654.325180 -654.325180 -627.837227 -627.837227 -548.373367   
12034 -521.885414 -521.885414 -495.397461 -495.397461 -495.397461 -495.397461   
2349  -336.365602 -336.365602 -312.637815 -312.637815 -312.637815 -336.365602   
64334   -7.235882   -7.235882   -7.235882   -7.235882   -7.235882   -7.235882   
...           ...         ...         ...         ...         ...         ...   
29110  -13.043256  -13.043256  -13.043256   -7.482866   -7.482866  -13.043256   
70152  326.151992  326.151992  365.498156  326.151992  326.151992  247.459664   
29087   -1.922477  -13.043256  -13.043256    3.637913   -1.922477  -74.207541   
67936   55.135647   55.135647   55.135647   55.135647   55.135647   46.225429   
36047   55.332661   55.332661   55.332661   55.332661   62.664237   55.332661   

          ACC1130     ACC1131      ACC114      ACC115      ACC116      ACC117  \
49519  379.431726  -55.301204  283.790

In [8]:
training = pd.concat([X_train, y_train], axis = 1)
training

ACC110      ACC111     ACC1110     ACC1111     ACC1112     ACC1113  \
49519  275.095822  257.706505  309.874457  335.958433  309.874457  214.233212   
10257 -627.837227 -680.813133 -866.228804 -707.301086 -548.373367 -548.373367   
12034 -495.397461 -495.397461 -495.397461 -521.885414 -495.397461 -495.397461   
2349  -312.637815 -336.365602 -348.229495 -360.093388 -300.773921 -336.365602   
64334   -7.235882   -7.235882   -7.235882   -7.235882   -7.235882   -7.235882   
...           ...         ...         ...         ...         ...         ...   
29110   -1.922477   -1.922477   -1.922477   -7.482866   -1.922477   -7.482866   
70152  247.459664  286.805828  286.805828  326.151992  326.151992  326.151992   
29087   -7.482866   14.758692  -13.043256  -68.647152   -7.482866  -18.603645   
67936   55.135647   55.135647   55.135647   46.225429   46.225429   55.135647   
36047   55.332661   55.332661   55.332661   55.332661   55.332661   55.332661   

          ACC1114     ACC1115     ACC1116     ACC1117     ACC1118     ACC1119  \
49519  257.706505  344.653091  370.737067  335.958433  318.569115  301.179798   
10257 -521.885414 -574.861320 -601.349274 -627.837227 -654.325180 -627.837227   
12034 -495.397461 -495.397461 -495.397461 -495.397461 -495.397461 -495.397461   
2349  -348.229495 -348.229495 -383.821175 -371.957282 -360.093388 -371.957282   
64334   -7.235882   -7.235882   -7.235882   -7.235882   -7.235882   -7.235882   
...           ...         ...         ...         ...         ...         ...   
29110   -7.482866   -7.482866   -1.922477   -7.482866  -13.043256  -13.043256   
70152  286.805828  326.151992  365.498156  365.498156  326.151992  286.805828   
29087   -7.482866   -1.922477   -7.482866   -7.482866   -1.922477   -1.922477   
67936   55.135647   55.135647   46.225429   55.135647   55.135647   55.135647   
36047   55.332661   55.332661   55.332661   55.332661   55.332661   55.332661   

           ACC112     ACC1120     ACC1121     ACC1122     ACC1123     ACC1124  \
49519  249.011847  266.401164  266.401164  266.401164  309.874457  327.263774   
10257 -707.301086 -627.837227 -627.837227 -627.837227 -627.837227 -627.837227   
12034 -495.397461 -495.397461 -495.397461 -495.397461 -495.397461 -495.397461   
2349  -348.229495 -383.821175 -371.957282 -383.821175 -348.229495 -360.093388   
64334   -7.235882   -7.235882   -7.235882   -7.235882   -7.235882   -7.235882   
...           ...         ...         ...         ...         ...         ...   
29110   -1.922477   -1.922477  -13.043256   -1.922477    3.637913   -7.482866   
70152  247.459664  326.151992  365.498156  365.498156  365.498156  365.498156   
29087    3.637913  -18.603645  -13.043256  -13.043256  -13.043256  -13.043256   
67936   55.135647   55.135647   55.135647   55.135647   46.225429   55.135647   
36047   62.664237   55.332661   55.332661   55.332661   55.332661   55.332661   

          ACC1125     ACC1126     ACC1127     ACC1128     ACC1129      ACC113  \
49519  335.958433  283.790481  301.179798  266.401164  196.843895  266.401164   
10257 -654.325180 -654.325180 -654.325180 -627.837227 -627.837227 -548.373367   
12034 -521.885414 -521.885414 -495.397461 -495.397461 -495.397461 -495.397461   
2349  -336.365602 -336.365602 -312.637815 -312.637815 -312.637815 -336.365602   
64334   -7.235882   -7.235882   -7.235882   -7.235882   -7.235882   -7.235882   
...           ...         ...         ...         ...         ...         ...   
29110  -13.043256  -13.043256  -13.043256   -7.482866   -7.482866  -13.043256   
70152  326.151992  326.151992  365.498156  326.151992  326.151992  247.459664   
29087   -1.922477  -13.043256  -13.043256    3.637913   -1.922477  -74.207541   
67936   55.135647   55.135647   55.135647   55.135647   55.135647   46.225429   
36047   55.332661   55.332661   55.332661   55.332661   62.664237   55.332661   

          ACC1130     ACC1131      ACC114      ACC115      ACC116      ACC117  \
49519  379.431726  -55.301204  283.790

In [9]:
validation = pd.concat([X_val, y_val], axis = 1)
validation

ACC110      ACC111     ACC1110     ACC1111     ACC1112     ACC1113  \
32214   40.669509   40.669509   40.669509   40.669509   40.669509   40.669509   
63688  -78.517629  -87.427847  -96.338066 -105.248284  -78.517629  -60.697192   
27515    9.198303    9.198303    9.198303    9.198303    9.198303    9.198303   
61689 -156.560821 -156.560821 -156.560821 -179.854328 -156.560821 -156.560821   
9886    54.208394   54.208394   54.208394   54.208394   54.208394   54.208394   
...           ...         ...         ...         ...         ...         ...   
9498  -533.443084 -533.443084 -533.443084 -533.443084 -533.443084 -533.443084   
26169  -24.164035  -24.164035  -24.164035  -24.164035  -24.164035  -24.164035   
7991   511.270654  543.917958  576.565263  576.565263  576.565263  576.565263   
25296 -905.378191 -905.378191 -905.378191 -933.632381 -905.378191 -905.378191   
8323   511.270654  543.917958  543.917958  543.917958  576.565263  543.917958   

          ACC1114     ACC1115     ACC1116     ACC1117     ACC1118     ACC1119  \
32214   40.669509   40.669509   40.669509   40.669509   40.669509   40.669509   
63688  -60.697192  -60.697192  -69.607411  -60.697192  -51.786974  -69.607411   
27515    9.198303    9.198303    9.198303    9.198303    9.198303    9.198303   
61689 -179.854328 -156.560821 -156.560821 -179.854328 -179.854328 -179.854328   
9886    21.561090   54.208394   54.208394   54.208394   54.208394   54.208394   
...           ...         ...         ...         ...         ...         ...   
9498  -533.443084 -533.443084 -533.443084 -533.443084 -533.443084 -533.443084   
26169  -24.164035  -24.164035  -24.164035  -24.164035  -24.164035  -29.724425   
7991   576.565263  576.565263  576.565263  576.565263  543.917958  543.917958   
25296 -933.632381 -933.632381 -905.378191 -933.632381 -933.632381 -905.378191   
8323   511.270654  543.917958  576.565263  576.565263  511.270654  543.917958   

           ACC112     ACC1120     ACC1121     ACC1122     ACC1123     ACC1124  \
32214   40.669509   40.669509   40.669509   40.669509   40.669509   40.669509   
63688  -96.338066  -87.427847  -60.697192  -69.607411  -42.876755  -33.966537   
27515    9.198303    9.198303    9.198303    9.198303    9.198303    9.198303   
61689 -156.560821 -179.854328 -156.560821 -179.854328 -156.560821 -179.854328   
9886    54.208394   54.208394   54.208394   54.208394   54.208394   54.208394   
...           ...         ...         ...         ...         ...         ...   
9498  -533.443084 -533.443084 -533.443084 -533.443084 -533.443084 -533.443084   
26169  -24.164035  -24.164035  -24.164035  -24.164035  -24.164035  -24.164035   
7991   543.917958  543.917958  543.917958  576.565263  576.565263  543.917958   
25296 -905.378191 -905.378191 -933.632381 -933.632381 -905.378191 -933.632381   
8323   576.565263  576.565263  543.917958  511.270654  576.565263  543.917958   

          ACC1125     ACC1126     ACC1127     ACC1128     ACC1129      ACC113  \
32214   40.669509   48.001085   48.001085   48.001085   40.669509   40.669509   
63688 -131.978939  -96.338066 -203.260686 -194.350468 -203.260686  -96.338066   
27515    9.198303    3.637913    9.198303    9.198303    9.198303    3.637913   
61689 -179.854328 -156.560821 -179.854328 -179.854328 -156.560821 -179.854328   
9886    54.208394   54.208394   54.208394   54.208394   54.208394   54.208394   
...           ...         ...         ...         ...         ...         ...   
9498  -533.443084 -533.443084 -533.443084 -533.443084 -533.443084 -533.443084   
26169  -24.164035  -24.164035  -29.724425  -29.724425  -24.164035  -24.164035   
7991   576.565263  576.565263  543.917958  543.917958  543.917958  543.917958   
25296 -933.632381 -933.632381 -905.378191 -933.632381 -933.632381 -905.378191   
8323   478.623350  543.917958  576.565263  543.917958  576.565263  576.565263   

          ACC1130     ACC1131      ACC114      ACC115      ACC116      ACC117  \
32214   40.669509   40.669509   48.001

In [10]:
test = pd.concat([X_test, y_test], axis = 1)
test

ACC110      ACC111     ACC1110     ACC1111     ACC1112     ACC1113  \
67820   55.135647   55.135647   55.135647   55.135647   55.135647   55.135647   
69736  404.844320  365.498156  365.498156  365.498156  365.498156  365.498156   
45334  231.906192  231.906192  231.906192  231.906192  231.906192  231.906192   
159    328.012431  280.556857  280.556857  185.645710  221.237390  256.829070   
8549   576.565263  576.565263  576.565263  576.565263  576.565263  576.565263   
...           ...         ...         ...         ...         ...         ...   
977    161.917923  161.917923  161.917923  161.917923  161.917923  173.781816   
70208  168.767337  168.767337  168.767337  168.767337  168.767337  168.767337   
41947 -174.028735 -174.028735 -174.028735 -174.028735 -174.028735 -174.028735   
34549   40.669509   48.001085  -61.972554   26.006357 -142.619890 -142.619890   
70724 -500.117448 -539.463612 -578.809776 -460.771284 -421.425120 -460.771284   

          ACC1114     ACC1115     ACC1116     ACC1117     ACC1118     ACC1119  \
67820   55.135647   55.135647   55.135647   55.135647   55.135647   55.135647   
69736  365.498156  404.844320  404.844320  404.844320  365.498156  365.498156   
45334  231.906192  231.906192  231.906192  231.906192  231.906192  231.906192   
159    256.829070  244.965177  292.420751  280.556857  363.604111  328.012431   
8549   576.565263  576.565263  576.565263  576.565263  576.565263  576.565263   
...           ...         ...         ...         ...         ...         ...   
977    161.917923  161.917923  161.917923  161.917923  161.917923  161.917923   
70208  168.767337  168.767337  168.767337  168.767337  168.767337  168.767337   
41947 -174.028735 -174.028735 -174.028735 -174.028735 -174.028735 -174.028735   
34549   55.332661   91.990541  187.301029  172.637877  128.648421   69.995813   
70724 -539.463612 -539.463612 -539.463612 -539.463612 -539.463612 -539.463612   

           ACC112     ACC1120     ACC1121     ACC1122     ACC1123     ACC1124  \
67820   55.135647   55.135647   55.135647   55.135647   55.135647   55.135647   
69736  365.498156  365.498156  365.498156  365.498156  365.498156  365.498156   
45334  231.906192  231.906192  231.906192  231.906192  231.906192  231.906192   
159    268.692964  328.012431  304.284644  280.556857  233.101284  197.509603   
8549   576.565263  576.565263  609.212567  576.565263  609.212567  576.565263   
...           ...         ...         ...         ...         ...         ...   
977    161.917923  161.917923  161.917923  161.917923  161.917923  161.917923   
70208  168.767337  168.767337  168.767337  168.767337  168.767337  168.767337   
41947 -174.028735 -174.028735 -174.028735 -174.028735 -174.028735 -174.028735   
34549   40.669509   48.001085    4.011629   -3.319947  -10.651523   18.674781   
70724 -539.463612 -578.809776 -539.463612 -500.117448 -539.463612 -539.463612   

          ACC1125     ACC1126     ACC1127     ACC1128     ACC1129      ACC113  \
67820   55.135647   55.135647   55.135647   55.135647   55.135647   55.135647   
69736  365.498156  365.498156  365.498156  365.498156  404.844320  365.498156   
45334  231.906192  231.906192  231.906192  231.906192  231.906192  231.906192   
159    150.054030  221.237390  233.101284  138.190136  138.190136  292.420751   
8549   576.565263  576.565263  576.565263  576.565263  576.565263  576.565263   
...           ...         ...         ...         ...         ...         ...   
977    161.917923  161.917923  161.917923  161.917923  161.917923  161.917923   
70208  168.767337  168.767337  168.767337  168.767337  168.767337  168.767337   
41947 -174.028735 -174.028735 -174.028735 -174.028735 -174.028735 -174.028735   
34549   55.332661  106.653693   91.990541   69.995813   40.669509   40.669509   
70724 -539.463612 -539.463612 -578.809776 -539.463612 -500.117448 -500.117448   

          ACC1130     ACC1131      ACC114      ACC115      ACC116      ACC117  \
67820   55.135647   55.135647   55.135

In [11]:
wesad = pd.concat([training, validation, test])
wesad

ACC110      ACC111     ACC1110     ACC1111     ACC1112     ACC1113  \
49519  275.095822  257.706505  309.874457  335.958433  309.874457  214.233212   
10257 -627.837227 -680.813133 -866.228804 -707.301086 -548.373367 -548.373367   
12034 -495.397461 -495.397461 -495.397461 -521.885414 -495.397461 -495.397461   
2349  -312.637815 -336.365602 -348.229495 -360.093388 -300.773921 -336.365602   
64334   -7.235882   -7.235882   -7.235882   -7.235882   -7.235882   -7.235882   
...           ...         ...         ...         ...         ...         ...   
977    161.917923  161.917923  161.917923  161.917923  161.917923  173.781816   
70208  168.767337  168.767337  168.767337  168.767337  168.767337  168.767337   
41947 -174.028735 -174.028735 -174.028735 -174.028735 -174.028735 -174.028735   
34549   40.669509   48.001085  -61.972554   26.006357 -142.619890 -142.619890   
70724 -500.117448 -539.463612 -578.809776 -460.771284 -421.425120 -460.771284   

          ACC1114     ACC1115     ACC1116     ACC1117     ACC1118     ACC1119  \
49519  257.706505  344.653091  370.737067  335.958433  318.569115  301.179798   
10257 -521.885414 -574.861320 -601.349274 -627.837227 -654.325180 -627.837227   
12034 -495.397461 -495.397461 -495.397461 -495.397461 -495.397461 -495.397461   
2349  -348.229495 -348.229495 -383.821175 -371.957282 -360.093388 -371.957282   
64334   -7.235882   -7.235882   -7.235882   -7.235882   -7.235882   -7.235882   
...           ...         ...         ...         ...         ...         ...   
977    161.917923  161.917923  161.917923  161.917923  161.917923  161.917923   
70208  168.767337  168.767337  168.767337  168.767337  168.767337  168.767337   
41947 -174.028735 -174.028735 -174.028735 -174.028735 -174.028735 -174.028735   
34549   55.332661   91.990541  187.301029  172.637877  128.648421   69.995813   
70724 -539.463612 -539.463612 -539.463612 -539.463612 -539.463612 -539.463612   

           ACC112     ACC1120     ACC1121     ACC1122     ACC1123     ACC1124  \
49519  249.011847  266.401164  266.401164  266.401164  309.874457  327.263774   
10257 -707.301086 -627.837227 -627.837227 -627.837227 -627.837227 -627.837227   
12034 -495.397461 -495.397461 -495.397461 -495.397461 -495.397461 -495.397461   
2349  -348.229495 -383.821175 -371.957282 -383.821175 -348.229495 -360.093388   
64334   -7.235882   -7.235882   -7.235882   -7.235882   -7.235882   -7.235882   
...           ...         ...         ...         ...         ...         ...   
977    161.917923  161.917923  161.917923  161.917923  161.917923  161.917923   
70208  168.767337  168.767337  168.767337  168.767337  168.767337  168.767337   
41947 -174.028735 -174.028735 -174.028735 -174.028735 -174.028735 -174.028735   
34549   40.669509   48.001085    4.011629   -3.319947  -10.651523   18.674781   
70724 -539.463612 -578.809776 -539.463612 -500.117448 -539.463612 -539.463612   

          ACC1125     ACC1126     ACC1127     ACC1128     ACC1129      ACC113  \
49519  335.958433  283.790481  301.179798  266.401164  196.843895  266.401164   
10257 -654.325180 -654.325180 -654.325180 -627.837227 -627.837227 -548.373367   
12034 -521.885414 -521.885414 -495.397461 -495.397461 -495.397461 -495.397461   
2349  -336.365602 -336.365602 -312.637815 -312.637815 -312.637815 -336.365602   
64334   -7.235882   -7.235882   -7.235882   -7.235882   -7.235882   -7.235882   
...           ...         ...         ...         ...         ...         ...   
977    161.917923  161.917923  161.917923  161.917923  161.917923  161.917923   
70208  168.767337  168.767337  168.767337  168.767337  168.767337  168.767337   
41947 -174.028735 -174.028735 -174.028735 -174.028735 -174.028735 -174.028735   
34549   55.332661  106.653693   91.990541   69.995813   40.669509   40.669509   
70724 -539.463612 -539.463612 -578.809776 -539.463612 -500.117448 -500.117448   

          ACC1130     ACC1131      ACC114      ACC115      ACC116      ACC117  \
49519  379.431726  -55.301204  283.790

In [13]:
wesad.to_csv("Final_CSVs/wesad_new_with1.csv", index = False)

In [14]:
wesad_test = pd.read_csv('Final_CSVs/wesad_new_with1.csv')

In [15]:
wesad_test

ACC110      ACC111     ACC1110     ACC1111     ACC1112     ACC1113  \
0      275.095822  257.706505  309.874457  335.958433  309.874457  214.233212   
1     -627.837227 -680.813133 -866.228804 -707.301086 -548.373367 -548.373367   
2     -495.397461 -495.397461 -495.397461 -521.885414 -495.397461 -495.397461   
3     -312.637815 -336.365602 -348.229495 -360.093388 -300.773921 -336.365602   
4       -7.235882   -7.235882   -7.235882   -7.235882   -7.235882   -7.235882   
...           ...         ...         ...         ...         ...         ...   
78761  161.917923  161.917923  161.917923  161.917923  161.917923  173.781816   
78762  168.767337  168.767337  168.767337  168.767337  168.767337  168.767337   
78763 -174.028735 -174.028735 -174.028735 -174.028735 -174.028735 -174.028735   
78764   40.669509   48.001085  -61.972554   26.006357 -142.619890 -142.619890   
78765 -500.117448 -539.463612 -578.809776 -460.771284 -421.425120 -460.771284   

          ACC1114     ACC1115     ACC1116     ACC1117     ACC1118     ACC1119  \
0      257.706505  344.653091  370.737067  335.958433  318.569115  301.179798   
1     -521.885414 -574.861320 -601.349274 -627.837227 -654.325180 -627.837227   
2     -495.397461 -495.397461 -495.397461 -495.397461 -495.397461 -495.397461   
3     -348.229495 -348.229495 -383.821175 -371.957282 -360.093388 -371.957282   
4       -7.235882   -7.235882   -7.235882   -7.235882   -7.235882   -7.235882   
...           ...         ...         ...         ...         ...         ...   
78761  161.917923  161.917923  161.917923  161.917923  161.917923  161.917923   
78762  168.767337  168.767337  168.767337  168.767337  168.767337  168.767337   
78763 -174.028735 -174.028735 -174.028735 -174.028735 -174.028735 -174.028735   
78764   55.332661   91.990541  187.301029  172.637877  128.648421   69.995813   
78765 -539.463612 -539.463612 -539.463612 -539.463612 -539.463612 -539.463612   

           ACC112     ACC1120     ACC1121     ACC1122     ACC1123     ACC1124  \
0      249.011847  266.401164  266.401164  266.401164  309.874457  327.263774   
1     -707.301086 -627.837227 -627.837227 -627.837227 -627.837227 -627.837227   
2     -495.397461 -495.397461 -495.397461 -495.397461 -495.397461 -495.397461   
3     -348.229495 -383.821175 -371.957282 -383.821175 -348.229495 -360.093388   
4       -7.235882   -7.235882   -7.235882   -7.235882   -7.235882   -7.235882   
...           ...         ...         ...         ...         ...         ...   
78761  161.917923  161.917923  161.917923  161.917923  161.917923  161.917923   
78762  168.767337  168.767337  168.767337  168.767337  168.767337  168.767337   
78763 -174.028735 -174.028735 -174.028735 -174.028735 -174.028735 -174.028735   
78764   40.669509   48.001085    4.011629   -3.319947  -10.651523   18.674781   
78765 -539.463612 -578.809776 -539.463612 -500.117448 -539.463612 -539.463612   

          ACC1125     ACC1126     ACC1127     ACC1128     ACC1129      ACC113  \
0      335.958433  283.790481  301.179798  266.401164  196.843895  266.401164   
1     -654.325180 -654.325180 -654.325180 -627.837227 -627.837227 -548.373367   
2     -521.885414 -521.885414 -495.397461 -495.397461 -495.397461 -495.397461   
3     -336.365602 -336.365602 -312.637815 -312.637815 -312.637815 -336.365602   
4       -7.235882   -7.235882   -7.235882   -7.235882   -7.235882   -7.235882   
...           ...         ...         ...         ...         ...         ...   
78761  161.917923  161.917923  161.917923  161.917923  161.917923  161.917923   
78762  168.767337  168.767337  168.767337  168.767337  168.767337  168.767337   
78763 -174.028735 -174.028735 -174.028735 -174.028735 -174.028735 -174.028735   
78764   55.332661  106.653693   91.990541   69.995813   40.669509   40.669509   
78765 -539.463612 -539.463612 -578.809776 -539.463612 -500.117448 -500.117448   

          ACC1130     ACC1131      ACC114      ACC115      ACC116      ACC117  \
0      379.431726  -55.301204  283.790

In [38]:
wesad_test.drop(['Unnamed: 0'], axis=1, inplace=True)

## User-based Models

In [5]:
unique_participants = wesad_dataset["id"].unique()
person_group = wesad_dataset.groupby('id')

In [6]:
accuracies_wesad = []
precision_wesad = []
recall_wesad = []
f1scores_wesad = []

for participant in unique_participants:
    print("Participant: ",participant)
    part_df = person_group.get_group(participant)
    grid = setup(data=part_df, target='stress', html=False, silent=True, verbose=False) #fix_imbalance = True,
    best = compare_models()
    accuracies_wesad.append(pull()['Accuracy'][0])
    precision_wesad.append(pull()['Prec.'][0])
    recall_wesad.append(pull()['Recall'][0])
    f1scores_wesad.append(pull()['F1'][0])
    print(best)

Participant:  2


Model  Accuracy     AUC  Recall   Prec.      F1   Kappa  \
lr  Logistic Regression     0.963  0.9953  0.9955  0.8749  0.9311  0.9059   

       MCC  TT (Sec)  
lr  0.9096     0.865

Model  Accuracy     AUC  Recall   Prec.      F1   Kappa  \
knn  K Neighbors Classifier     1.000  1.0000  1.0000  1.0000  1.0000  1.0000   
lr      Logistic Regression     0.963  0.9953  0.9955  0.8749  0.9311  0.9059   

        MCC  TT (Sec)  
knn  1.0000     0.371  
lr   0.9096     0.865

Model  Accuracy     AUC  Recall   Prec.      F1   Kappa  \
knn  K Neighbors Classifier    1.0000  1.0000  1.0000  1.0000  1.0000  1.0000   
nb              Naive Bayes    0.9904  0.9973  0.9661  0.9954  0.9804  0.9741   
lr      Logistic Regression    0.9630  0.9953  0.9955  0.8749  0.9311  0.9059   

        MCC  TT (Sec)  
knn  1.0000     0.371  
nb   0.9743     0.018  
lr   0.9096     0.865

Model  Accuracy     AUC  Recall   Prec.      F1  \
knn    K Neighbors Classifier    1.0000  1.0000  1.0000  1.0000  1.0000   
dt   Decision Tree Classifier    0.9958  0.9934  0.9887  0.9944  0.9915   
nb                Naive Bayes    0.9904  0.9973  0.9661  0.9954  0.9804   
lr        Logistic Regression    0.9630  0.9953  0.9955  0.8749  0.9311   

      Kappa     MCC  TT (Sec)  
knn  1.0000  1.0000     0.371  
dt   0.9887  0.9887     0.028  
nb   0.9741  0.9743     0.018  
lr   0.9059  0.9096     0.865

...

Model  Accuracy     AUC  Recall   Prec.  \
gbc       Gradient Boosting Classifier    0.9894  0.9984  0.9772  0.9842   
ada               Ada Boost Classifier    0.9835  0.9944  0.9653  0.9741   
rf            Random Forest Classifier    0.9832  0.9984  0.9624  0.9760   
knn             K Neighbors Classifier    0.9826  0.9865  0.9515  0.9849   
dt            Decision Tree Classifier    0.9797  0.9727  0.9574  0.9684   
et              Extra Trees Classifier    0.9759  0.9972  0.9614  0.9513   
ridge                 Ridge Classifier    0.8514  0.0000  0.5317  0.8771   
lda       Linear Discriminant Analysis    0.8357  0.8310  0.5525  0.7848   
lr                 Logistic Regression    0.8080  0.8580  0.6178  0.6603   
qda    Quadratic Discriminant Analysis    0.7758  0.9159  0.3792  0.6581   
nb                         Naive Bayes    0.7237  0.8349  0.7030  0.4966   
svm                SVM - Linear Kernel    0.6017  0.0000  0.5911  0.3614   

           F1   Kappa     MCC  TT (Sec)  
gbc    0.9806  0.9733  0.9734     1.034  
ada    0.9696  0.9583  0.9584     0.246  
rf     0.9691  0.9575  0.9576     0.191  
knn    0.9677  0.9559  0.9563     0.054  
dt     0.9627  0.9487  0.9489     0.047  
et     0.9563  0.9396  0.9397     0.109  
ridge  0.6614  0.5736  0.6034     0.027  
lda    0.6476  0.5448  0.5596     0.043  
lr     0.6379  0.5076  0.5084     0.200  
qda    0.4798  0.3502  0.3724     0.031  
nb     0.5814  0.3842  0.3979     0.016  
svm    0.4445  0.1624  0.1796     0.043

Model  Accuracy     AUC  Recall   Prec.  \
lightgbm  Light Gradient Boosting Machine    0.9924  0.9993  0.9891  0.9835   
gbc          Gradient Boosting Classifier    0.9894  0.9984  0.9772  0.9842   
ada                  Ada Boost Classifier    0.9835  0.9944  0.9653  0.9741   
rf               Random Forest Classifier    0.9832  0.9984  0.9624  0.9760   
knn                K Neighbors Classifier    0.9826  0.9865  0.9515  0.9849   
dt               Decision Tree Classifier    0.9797  0.9727  0.9574  0.9684   
et                 Extra Trees Classifier    0.9759  0.9972  0.9614  0.9513   
ridge                    Ridge Classifier    0.8514  0.0000  0.5317  0.8771   
lda          Linear Discriminant Analysis    0.8357  0.8310  0.5525  0.7848   
lr                    Logistic Regression    0.8080  0.8580  0.6178  0.6603   
qda       Quadratic Discriminant Analysis    0.7758  0.9159  0.3792  0.6581   
nb                            Naive Bayes    0.7237  0.8349  0.7030  0.4966   
svm                   SVM - Linear Kernel    0.6017  0.0000  0.5911  0.3614   

              F1   Kappa     MCC  TT (Sec)  
lightgbm  0.9862  0.9810  0.9811     0.244  
gbc       0.9806  0.9733  0.9734     1.034  
ada       0.9696  0.9583  0.9584     0.246  
rf        0.9691  0.9575  0.9576     0.191  
knn       0.9677  0.9559  0.9563     0.054  
dt        0.9627  0.9487  0.9489     0.047  
et        0.9563  0.9396  0.9397     0.109  
ridge     0.6614  0.5736  0.6034     0.027  
lda       0.6476  0.5448  0.5596     0.043  
lr        0.6379  0.5076  0.5084     0.200  
qda       0.4798  0.3502  0.3724     0.031  
nb        0.5814  0.3842  0.3979     0.016  
svm       0.4445  0.1624  0.1796     0.043

Model  Accuracy     AUC  Recall   Prec.  \
lightgbm  Light Gradient Boosting Machine    0.9924  0.9993  0.9891  0.9835   
gbc          Gradient Boosting Classifier    0.9894  0.9984  0.9772  0.9842   
ada                  Ada Boost Classifier    0.9835  0.9944  0.9653  0.9741   
rf               Random Forest Classifier    0.9832  0.9984  0.9624  0.9760   
knn                K Neighbors Classifier    0.9826  0.9865  0.9515  0.9849   
dt               Decision Tree Classifier    0.9797  0.9727  0.9574  0.9684   
et                 Extra Trees Classifier    0.9759  0.9972  0.9614  0.9513   
ridge                    Ridge Classifier    0.8514  0.0000  0.5317  0.8771   
lda          Linear Discriminant Analysis    0.8357  0.8310  0.5525  0.7848   
lr                    Logistic Regression    0.8080  0.8580  0.6178  0.6603   
qda       Quadratic Discriminant Analysis    0.7758  0.9159  0.3792  0.6581   
dummy                    Dummy Classifier    0.7261  0.5000  0.0000  0.0000   
nb                            Naive Bayes    0.7237  0.8349  0.7030  0.4966   
svm                   SVM - Linear Kernel    0.6017  0.0000  0.5911  0.3614   

              F1   Kappa     MCC  TT (Sec)  
lightgbm  0.9862  0.9810  0.9811     0.244  
gbc       0.9806  0.9733  0.9734     1.034  
ada       0.9696  0.9583  0.9584     0.246  
rf        0.9691  0.9575  0.9576     0.191  
knn       0.9677  0.9559  0.9563     0.054  
dt        0.9627  0.9487  0.9489     0.047  
et        0.9563  0.9396  0.9397     0.109  
ridge     0.6614  0.5736  0.6034     0.027  
lda       0.6476  0.5448  0.5596     0.043  
lr        0.6379  0.5076  0.5084     0.200  
qda       0.4798  0.3502  0.3724     0.031  
dummy     0.0000  0.0000  0.0000     0.017  
nb        0.5814  0.3842  0.3979     0.016  
svm       0.4445  0.1624  0.1796     0.043

Model  Accuracy     AUC  Recall   Prec.  \
lightgbm  Light Gradient Boosting Machine    0.9924  0.9993  0.9891  0.9835   
gbc          Gradient Boosting Classifier    0.9894  0.9984  0.9772  0.9842   
ada                  Ada Boost Classifier    0.9835  0.9944  0.9653  0.9741   
rf               Random Forest Classifier    0.9832  0.9984  0.9624  0.9760   
knn                K Neighbors Classifier    0.9826  0.9865  0.9515  0.9849   
dt               Decision Tree Classifier    0.9797  0.9727  0.9574  0.9684   
et                 Extra Trees Classifier    0.9759  0.9972  0.9614  0.9513   
ridge                    Ridge Classifier    0.8514  0.0000  0.5317  0.8771   
lda          Linear Discriminant Analysis    0.8357  0.8310  0.5525  0.7848   
lr                    Logistic Regression    0.8080  0.8580  0.6178  0.6603   
qda       Quadratic Discriminant Analysis    0.7758  0.9159  0.3792  0.6581   
dummy                    Dummy Classifier    0.7261  0.5000  0.0000  0.0000   
nb                            Naive Bayes    0.7237  0.8349  0.7030  0.4966   
svm                   SVM - Linear Kernel    0.6017  0.0000  0.5911  0.3614   

              F1   Kappa     MCC  TT (Sec)  
lightgbm  0.9862  0.9810  0.9811     0.244  
gbc       0.9806  0.9733  0.9734     1.034  
ada       0.9696  0.9583  0.9584     0.246  
rf        0.9691  0.9575  0.9576     0.191  
knn       0.9677  0.9559  0.9563     0.054  
dt        0.9627  0.9487  0.9489     0.047  
et        0.9563  0.9396  0.9397     0.109  
ridge     0.6614  0.5736  0.6034     0.027  
lda       0.6476  0.5448  0.5596     0.043  
lr        0.6379  0.5076  0.5084     0.200  
qda       0.4798  0.3502  0.3724     0.031  
dummy     0.0000  0.0000  0.0000     0.017  
nb        0.5814  0.3842  0.3979     0.016  
svm       0.4445  0.1624  0.1796     0.043

LGBMClassifier(boosting_type='gbdt', class_weight=None, colsample_bytree=1.0,
               importance_type='split', learning_rate=0.1, max_depth=-1,
               min_child_samples=20, min_child_weight=0.001, min_split_gain=0.0,
               n_estimators=100, n_jobs=-1, num_leaves=31, objective=None,
               random_state=1251, reg_alpha=0.0, reg_lambda=0.0, silent='warn',
               subsample=1.0, subsample_for_bin=200000, subsample_freq=0)


In [7]:
mean_acc_wesad = statistics.mean(accuracies_wesad)
mean_prec_wesad = statistics.mean(precision_wesad)
mean_rec_wesad = statistics.mean(recall_wesad)
mean_f1_wesad = statistics.mean(f1scores_wesad)
std_acc_wesad = statistics.stdev(accuracies_wesad)
std_prec_wesad = statistics.stdev(precision_wesad)
std_rec_wesad = statistics.stdev(recall_wesad)
std_f1_wesad = statistics.stdev(f1scores_wesad)

In [8]:
print("Mean Accuracy WESAD: ",mean_acc_wesad)
print("Mean Precision WESAD: ",mean_prec_wesad)
print("Mean Recall WESAD: ",mean_rec_wesad)
print("Mean F1-score WESAD: ",mean_f1_wesad)
print("Standard deviation of Accuracy WESAD: ",std_acc_wesad)
print("Standard deviation of Precision WESAD: ",std_prec_wesad)
print("Standard deviation of Recall WESAD: ",std_rec_wesad)
print("Standard deviation of F1-score WESAD: ",std_f1_wesad)

Mean Accuracy WESAD:  0.9909266666666666
Mean Precision WESAD:  0.9824933333333333
Mean Recall WESAD:  0.98158
Mean F1-score WESAD:  0.98194
Standard deviation of Accuracy WESAD:  0.018745379113137135
Standard deviation of Precision WESAD:  0.036487462947990136
Standard deviation of Recall WESAD:  0.03900875725855854
Standard deviation of F1-score WESAD:  0.03776891768183387


In [9]:
accuracies_wesad

[1.0,
 1.0,
 0.9967,
 1.0,
 0.9984,
 0.9992,
 1.0,
 0.9967,
 0.9944,
 1.0,
 0.9345,
 0.9989,
 0.9586,
 0.9941,
 0.9924]

# ADARP

In [2]:
adarp_dataset = pd.read_csv('Final_CSVs/adarp_id.csv')

In [3]:
adarp_dataset

id       EDA_0       EDA_1       EDA_2       EDA_3       EDA_4  \
0       8  279.693630  279.693630  277.263096  278.536233  277.263096   
1       1  -26.705520   -8.030028    9.632398   26.103795   19.179108   
2       4  424.691455  423.525565  424.108510  423.525565  423.525565   
3       8  -96.859455  -96.743625  -96.743625  -95.932633  -95.932633   
4       3 -110.091983 -109.777949 -111.034574 -110.406261 -109.463670   
...    ..         ...         ...         ...         ...         ...   
16352   7  -50.075140  -49.147074  -51.374547  -50.817679  -50.260811   
16353   6   28.103361   35.282196   47.029379   70.523745   77.547103   
16354   1  -42.740826  -42.740826  -42.652498  -42.784973  -42.784973   
16355   5  -63.990278  -63.568335  -63.779307  -63.990278  -63.779307   
16356   7    9.078313    9.820562   12.418363   15.387361   16.686334   

            EDA_5       EDA_6       EDA_7       EDA_8       EDA_9      EDA_10  \
0      275.411261  274.253774  270.434365  275.642741  276.337179  273.906555   
1        6.905367   16.839128   32.247524   -1.041654   22.086138   39.576458   
2      422.651376  422.359904  422.068431  421.485487  421.194015  418.279519   
3      -95.469222  -95.353392  -94.889891  -94.889891  -94.774061  -94.889891   
4     -107.578732 -105.379515 -104.436924 -102.551986 -100.981081 -100.038490   
...           ...         ...         ...         ...         ...         ...   
16352  -50.632153  -50.817679  -50.260811  -50.260811  -50.446482  -50.260811   
16353   49.484387   14.569084   55.847477   21.421672   32.516233    6.085007   
16354  -42.784973  -42.784973  -42.784973  -42.784973  -42.784973  -42.740826   
16355  -63.779307  -63.779307  -63.357364  -63.990278  -63.779307  -63.779307   
16356   18.913083   19.840859   21.511029   25.778855   25.222277   26.150052   

           EDA_11      EDA_12      EDA_13      EDA_14      EDA_15      EDA_16  \
0      274.832473  273.559336  272.864898  273.559336  272.517679  272.401939   
1       19.983846   -0.202799  -17.869706    1.641230    9.588252   12.593879   
2      417.988274  418.862464  417.113857  415.947968  415.656723  414.782307   
3      -94.774061  -94.426480  -94.774061  -94.774061  -94.310650  -94.774061   
4      -99.096143  -97.525239  -96.582648  -97.525239  -96.896927  -95.326022   
...           ...         ...         ...         ...         ...         ...   
16352  -50.817679  -50.632153  -50.260811  -50.260811  -50.817679  -50.817679   
16353   -6.641171   -3.385711  -24.922214    5.587863   13.419319  -19.048622   
16354  -42.740826  -42.740826  -42.784973  -42.784973  -42.740826  -42.652498   
16355  -63.779307  -63.779307  -63.779307  -63.357364  -63.990278  -63.990278   
16356   24.665553   25.778855   25.036606   26.150052   25.778855   27.820078   

           EDA_17      EDA_18      EDA_19      EDA_20      EDA_21      EDA_22  \
0      271.823241  271.128803  270.550104  269.739836  269.045398  268.466700   
1      -17.869706  -17.961445  -21.140247  -19.904037  -31.118154  -38.228698   
2      419.153936  414.490834  408.370599  406.330520  403.416025  402.541835   
3      -94.774061  -94.774061  -94.774061  -94.774061  -94.889891  -94.774061   
4      -92.498493  -90.613310  -89.356684  -87.785780  -86.215121  -84.958251   
...           ...         ...         ...         ...         ...         ...   
16352  -50.260811  -50.632153  -49.889613  -51.003350  -50.446482  -50.817679   
16353   36.097940   15.377183   45.234639   12.114076   16.845676   33.324332   
16354  -42.740826  -42.740826  -42.696645  -42.740826  -42.740826  -42.696645   
16355  -63.990278  -63.779307  -63.146557  -63.779307  -63.779307  -63.779307   
16356   26.892302   26.706776   28.376801   27.634552   29.675774   26.706776   

           EDA_23      EDA_24      EDA_25      EDA_26      EDA_27      EDA_28  \
0      267.772262  267.309303  268.235220  272.286200  272.980638  273.212117   
1      -31.208860  -36.595168  -11.252977   -5.51

In [4]:
# Train - Test Spilt for Deep Learning Implementation

X = adarp_dataset[adarp_dataset.columns.difference(['stress'])]
y = adarp_dataset["stress"]

X_train1, X_test, y_train1, y_test = train_test_split(X, y, test_size=0.25, random_state=123)
#X_train, X_val, y_train, y_val = train_test_split(X_train1, y_train1, test_size=0.15, random_state=123)



## Preprocessing

In [5]:
X_train1

ACC1_0      ACC1_1     ACC1_10    ACC1_100   ACC1_1000   ACC1_1001  \
7374  -448.138273 -429.315457 -372.847012 -466.961088 -664.600648 -589.309387   
5428   452.572425  461.468052  452.572425  452.572425  461.468052  452.572425   
2693  -163.388005 -155.994230 -104.237804  -74.662703  -96.844028  -96.844028   
12345 -570.424599 -570.424599 -561.528973 -552.633346 -579.320225 -579.320225   
6225  -659.158377 -615.990083 -626.782156 -303.019953 -108.762630 -292.227879   
...           ...         ...         ...         ...         ...         ...   
12252 -250.498713 -250.498713 -241.087305 -231.675898 -194.030267 -184.618860   
1346  -214.840455 -214.840455 -198.939409 -183.038363 -204.239757 -188.338711   
11646   63.910545   74.702618   31.534325   42.326398  117.870912  107.078839   
15725 -525.946467 -525.946467 -525.946467 -525.946467 -454.781457 -401.407699   
3582  -126.533399 -117.858641 -135.208156 -100.509127 -135.208156 -135.208156   

        ACC1_1002   ACC1_1003   ACC1_1004   ACC1_1005   ACC1_1006   ACC1_1007  \
7374  -419.904050 -325.789974 -241.087305 -306.967159 -476.372496 -476.372496   
5428   452.572425  452.572425  452.572425  452.572425  452.572425  452.572425   
2693  -104.237804 -104.237804 -104.237804 -104.237804  -96.844028 -104.237804   
12345 -579.320225 -579.320225 -579.320225 -579.320225 -579.320225 -579.320225   
6225  -346.188246 -313.812026 -324.604099 -324.604099 -303.019953 -249.059585   
...           ...         ...         ...         ...         ...         ...   
12252 -194.030267 -184.618860 -194.030267 -194.030267 -194.030267 -194.030267   
1346  -188.338711 -198.939409 -204.239757 -204.239757 -209.540106 -204.239757   
11646  107.078839  107.078839  107.078839  117.870912  117.870912  117.870912   
15725 -267.973305 -187.912668 -161.225789 -259.077678 -392.512073 -579.320225   
3582  -135.208156 -135.208156 -126.533399 -135.208156 -143.882913 -135.208156   

        ACC1_1008   ACC1_1009    ACC1_101   ACC1_1010   ACC1_1011   ACC1_1012  \
7374  -401.081235 -288.144343 -457.549680 -306.967159 -250.498713 -241.087305   
5428   452.572425  452.572425  452.572425  452.572425  452.572425  452.572425   
2693  -104.237804 -104.237804 -104.237804 -104.237804 -104.237804 -104.237804   
12345 -579.320225 -579.320225 -525.946467 -579.320225 -579.320225 -579.320225   
6225  -259.851659 -249.059585 -270.643732 -281.435806 -324.604099 -313.812026   
...           ...         ...         ...         ...         ...         ...   
12252 -194.030267 -194.030267 -231.675898 -194.030267 -194.030267 -194.030267   
1346  -204.239757 -198.939409 -188.338711 -204.239757 -204.239757 -204.239757   
11646  117.870912  107.078839   20.742251  107.078839   96.286765   96.286765   
15725 -428.094578 -365.825194 -525.946467 -303.555810 -419.198952 -401.407699   
3582  -126.533399 -135.208156  -74.484855 -135.208156 -135.208156 -135.208156   

        ACC1_1013   ACC1_1014   ACC1_1015   ACC1_1016   ACC1_1017   ACC1_1018  \
7374  -306.967159 -391.669827 -645.777833 -598.720794 -523.429534 -514.018126   
5428   452.572425  452.572425  452.572425  452.572425  452.572425  452.572425   
2693  -104.237804 -104.237804 -104.237804 -104.237804 -111.631579 -104.237804   
12345 -579.320225 -579.320225 -579.320225 -579.320225 -579.320225 -579.320225   
6225  -335.396173 -356.980320 -378.564467 -367.772393 -400.148614 -432.524834   
...           ...         ...         ...         ...         ...         ...   
12252 -194.030267 -194.030267 -194.030267 -194.030267 -194.030267 -184.618860   
1346  -209.540106 -198.939409 -193.639060 -220.140804 -204.239757 -188.338711   
11646  107.078839   96.286765   96.286765   96.286765   96.286765   96.286765   
15725 -348.033941 -374.720820 -481.468336 -401.407699 -348.033941 -205.703921   
3582  -135.208156 -126.533399 -135.208156 -135.208156 -135.208156 -135.208156   

        ACC1_1019    ACC1_102   ACC1_1020   ACC1_1021   ACC1_1022   ACC1_1023  \
7374  -570.486572 -410.492642 -542.252

In [6]:
id_train = X_train1["id"]
id_test = X_test["id"]

X_train1 = X_train1.drop('id', axis=1)
X_test = X_test.drop('id', axis=1)

### Scaling

In [7]:
from sklearn.preprocessing import StandardScaler

scaler = StandardScaler()
X_train1[:] = scaler.fit_transform(X_train1)
X_test[:] = scaler.transform(X_test)

### Principal Component Analysis (PCA)

In [8]:
from sklearn.decomposition import PCA

pca = PCA(n_components=250)
X_train1 = pd.DataFrame(pca.fit_transform(X_train1), index=X_train1.index)
X_test = pd.DataFrame(pca.transform(X_test), index=X_test.index)

In [10]:
X_test

0           1          2          3          4          5    \
3416    0.189704   28.919616  10.533361  -7.927332   0.939890   1.211739   
15511  -3.106853   16.456593 -51.898294  -4.080210   5.370143   3.674215   
358   -18.604962  -27.935620  -2.691609   2.362909  -5.336133 -35.291964   
15967 -48.009839  143.476229  65.999959 -15.906573  14.380782  -0.519988   
3381   43.719272   71.439656  21.334669  -6.188984   3.181794  14.267478   
...          ...         ...        ...        ...        ...        ...   
14994 -14.183324   69.585348  32.609356  -3.750749   0.883306   0.031458   
15649   6.289888  -32.050495  87.843617   4.951944  -9.923721  16.940356   
1636  -52.526937  117.548782 -19.696015   9.568756 -21.686070   3.745054   
4581  -28.249098  -26.997105  54.082033   0.550082  -1.863535  -0.258588   
10215 -26.644633   42.590907 -24.583798   0.828119   2.140673   1.620500   

             6         7         8          9          10        11   \
3416    1.333441  2.564118 -6.411406   2.876855   0.956919  3.101259   
15511  -5.265217 -2.139120 -5.117588  10.340013   5.396825  2.345248   
358   -10.003569  9.441992  5.145907  -5.573095  -0.127377 -2.289430   
15967  -0.661647  0.508402 -0.389674   2.632044  -0.332601 -0.677930   
3381    9.211625 -2.142807  5.209670  -5.162856   1.323166  1.311630   
...          ...       ...       ...        ...        ...       ...   
14994  -0.639752  0.862550 -0.214938   1.032628  -0.194594 -0.607700   
15649   0.339763 -3.149450  8.660654  -0.037309   8.172703 -1.844126   
1636    2.493357  2.038464 -3.945271   3.929809   1.985667  0.674231   
4581    0.668584 -0.656412 -1.946633  -0.691243   0.201905 -0.066365   
10215  -0.330326  6.011797  6.592117  -0.954890 -13.776599 -8.848120   

            12         13         14         15         16        17   \
3416  -8.529234 -10.583074   1.932693  10.136539  -8.881020 -4.356402   
15511 -4.731179   3.715194   6.629870   1.749660   0.799742  2.181873   
358   -7.132261   3.044687   2.973517  -0.862779  -0.550246 -0.069629   
15967 -0.954025  -0.220590   1.159120  -0.038798  -0.510907  0.218608   
3381  -0.737458   8.526027  20.542059  -5.798982  -2.704614  4.019638   
...         ...        ...        ...        ...        ...       ...   
14994 -0.833191  -0.069196   0.332684  -0.116035  -0.117034  0.333213   
15649 -6.727844   1.379952  -1.525506  -1.715238   2.086551  2.428031   
1636  -4.529271   1.112313   2.443504  -0.393933   0.068022  1.684910   
4581  -0.306087   1.175810   0.228122  -0.438980   2.653260  1.390343   
10215  0.356365  -1.333549  -2.903368   7.527666  12.063146 -9.978130   

             18        19        20        21        22        23        24   \
3416    7.414614 -0.804898  2.149031  7.666741 -1.248036  2.837029  9.764282   
15511  -0.523960  6.647873 -2.261647 -6.332039  0.955492  0.860502 -7.772997   
358    -1.097204 -0.386541  0.296051  0.340816  1.588254  0.728344  1.311609   
15967   0.204927 -0.234617 -0.002591 -0.034558 -0.151341 -0.035863 -0.005164   
3381  -11.470925 -0.980102 -2.816019 -3.177117  4.505310 -4.087712 -1.039586   
...          ...       ...       ...       ...       ...       ...       ...   
14994   0.109178  0.044666  0.224984 -0.190616 -0.223395 -0.155622  0.089339   
15649  -0.347751  0.872738 -2.066843 -8.397568 -3.531681 -3.633328 -0.423106   
1636    1.034275  0.206830 -1.345586  0.378361  2.865062  2.412611  1.954568   
4581    2.351748 -1.443245  0.719894  0.481333  0.915609 -0.771436  1.976221   
10215   2.430197 -9.358362 -8.325772 -0.068952  1.464650  1.855198  5.490620   

             25        26        27        28        29        30        31   \
3416    6.431411  0.714642 -0.439375 -3.830394  2.527980  0.769800  1.357126   
15511  -2.515668 -4.242662  6.147079  5.774697 -1.870870 -1.086034  2.085153   
358    -0.693477 -0.368449 -0.055756  0.491074  0.155461  1.285336  0.896732   
15967   0.207313  0.162634  0.197082 -0.047215  0.007806 -0.098436 -0.116947 

In [11]:
training = pd.concat([X_train1, y_train1],  ignore_index=True, axis = 1)
training

0          1          2          3          4          5    \
7374  -35.403967 -13.584755  11.910533  15.136094 -19.069353   4.406298   
5428   55.610077  31.351634  26.920716   6.137208 -21.156738   1.107372   
2693  -43.281369 -39.818919  32.249032   6.423005  -3.829736   4.179722   
12345 -75.210136  15.136503 -38.415731  -8.922326  -5.404721  27.737543   
6225  -35.006798  -9.199985 -15.419808  -2.743428   1.848794  31.206351   
...          ...        ...        ...        ...        ...        ...   
12252   0.045023  11.480156 -61.056940  10.162713 -10.111038   1.750809   
1346  -18.569692 -10.010034  -9.029104  -0.890967  -0.410305  -9.940186   
11646  -6.948346 -21.734892  47.836677   0.849393  -0.257242   4.994360   
15725 -73.976934  36.657368 -30.053970  -2.673558 -16.996494  14.263030   
3582  -38.876037 -16.368784  30.319440   2.665910  -7.007485  -0.832666   

             6          7          8         9          10         11   \
7374   39.507693 -14.858302   1.806010  0.578914  -6.761735 -10.927161   
5428   -0.616943   0.106355  -0.049682 -0.233233   0.386998  -0.835869   
2693   -1.178977   6.608860  -4.258251 -0.727822  -0.720481   2.712079   
12345  -0.152429  -3.538195  -8.038406 -1.110223  10.422630  -2.272864   
6225  -20.070332  19.967185 -18.206790 -2.159510 -26.930513   6.236844   
...          ...        ...        ...       ...        ...        ...   
12252   0.291299  -0.397514   0.238101  5.529392  -0.012417   4.954887   
1346   16.982668  -5.449044 -10.091026 -2.317217  -1.253335  -3.909347   
11646 -12.595930 -15.892247   8.285569  8.383630   1.287905  -7.678919   
15725   0.630004  -0.536571  -3.776405  1.725464  -4.255852   3.299784   
3582   -1.441021  -0.172129   0.248506 -1.231861  -1.289785  -0.805364   

             12         13         14         15         16         17   \
7374   10.178226   5.268345  18.744348   6.858127  -8.946382  -7.259109   
5428    0.043874  -0.121081  -1.106638   0.573177  -1.035813   1.245317   
2693   -1.521475   0.254781   0.243961  -3.569457   4.764510 -16.038955   
12345  -3.534238   4.808194  -0.618167  10.643919 -10.097375  -3.560674   
6225  -13.486625  13.091657  -1.850064   0.179548   2.903000   4.790746   
...          ...        ...        ...        ...        ...        ...   
12252  -2.015776  -1.966644   1.187858  -0.375836  -0.177199  -0.403895   
1346    1.109977   5.272019   1.249749   2.808767   5.170466  -6.267594   
11646  -0.808912   1.250632   0.506885  -1.418828  -3.539616  -0.049873   
15725   4.915212  -0.792421  -0.100772   4.403887   4.812652  -5.815247   
3582   -0.049259  -0.698291  -0.393727  -0.331023   1.694062  -0.560030   

            18        19        20         21        22         23   \
7374  -8.184188  1.339670 -2.650320   5.446167  6.565906   6.593064   
5428  -2.273136 -0.136379 -0.350567   2.753382 -1.266026  -1.341330   
2693  -0.530525  7.651406 -5.363283   0.852567 -0.311175   3.406032   
12345  0.214142 -7.941726 -0.514704  -4.148396  2.769721  -3.244688   
6225   2.169803 -1.273002  1.711290 -15.179893 -5.343740 -15.993336   
...         ...       ...       ...        ...       ...        ...   
12252 -0.640685 -0.721665  0.501587  -0.363929  0.798553  -1.886961   
1346   1.323211 -4.115852  2.077801  -9.006841 -8.827802   7.021431   
11646  0.995993  1.633953 -1.906225   0.835400 -2.062191   1.198091   
15725 -7.353508  3.612080  0.136487   2.945338  8.629677  -4.846002   
3582  -2.974892  0.121213  0.220461   0.369136 -1.455838  -1.887068   

             24         25         26         27         28         29   \
7374   -5.430837   0.905905  13.358457  -0.641665   0.748280  -2.976000   
5428    3.111043   1.194693  -3.292270   0.254575  -1.174591   0.480435   
2693   -0.218074   3.126443   9.160987  -2.840762  -1.936064 -11.259466   
12345  -5.299582  -5.271023   9.037873   7.288520   2.031449   0.145757   
6225   -1.742064   3.278709  -6.450616   3.512379  -0.694444   8.895505   
...          ...   

In [12]:
training.columns = [*training.columns[:-1], 'stress']

In [13]:
training = pd.concat([training, id_train],  axis = 1)
training

0          1          2          3          4          5  \
7374  -35.403967 -13.584755  11.910533  15.136094 -19.069353   4.406298   
5428   55.610077  31.351634  26.920716   6.137208 -21.156738   1.107372   
2693  -43.281369 -39.818919  32.249032   6.423005  -3.829736   4.179722   
12345 -75.210136  15.136503 -38.415731  -8.922326  -5.404721  27.737543   
6225  -35.006798  -9.199985 -15.419808  -2.743428   1.848794  31.206351   
...          ...        ...        ...        ...        ...        ...   
12252   0.045023  11.480156 -61.056940  10.162713 -10.111038   1.750809   
1346  -18.569692 -10.010034  -9.029104  -0.890967  -0.410305  -9.940186   
11646  -6.948346 -21.734892  47.836677   0.849393  -0.257242   4.994360   
15725 -73.976934  36.657368 -30.053970  -2.673558 -16.996494  14.263030   
3582  -38.876037 -16.368784  30.319440   2.665910  -7.007485  -0.832666   

               6          7          8         9         10         11  \
7374   39.507693 -14.858302   1.806010  0.578914  -6.761735 -10.927161   
5428   -0.616943   0.106355  -0.049682 -0.233233   0.386998  -0.835869   
2693   -1.178977   6.608860  -4.258251 -0.727822  -0.720481   2.712079   
12345  -0.152429  -3.538195  -8.038406 -1.110223  10.422630  -2.272864   
6225  -20.070332  19.967185 -18.206790 -2.159510 -26.930513   6.236844   
...          ...        ...        ...       ...        ...        ...   
12252   0.291299  -0.397514   0.238101  5.529392  -0.012417   4.954887   
1346   16.982668  -5.449044 -10.091026 -2.317217  -1.253335  -3.909347   
11646 -12.595930 -15.892247   8.285569  8.383630   1.287905  -7.678919   
15725   0.630004  -0.536571  -3.776405  1.725464  -4.255852   3.299784   
3582   -1.441021  -0.172129   0.248506 -1.231861  -1.289785  -0.805364   

              12         13         14         15         16         17  \
7374   10.178226   5.268345  18.744348   6.858127  -8.946382  -7.259109   
5428    0.043874  -0.121081  -1.106638   0.573177  -1.035813   1.245317   
2693   -1.521475   0.254781   0.243961  -3.569457   4.764510 -16.038955   
12345  -3.534238   4.808194  -0.618167  10.643919 -10.097375  -3.560674   
6225  -13.486625  13.091657  -1.850064   0.179548   2.903000   4.790746   
...          ...        ...        ...        ...        ...        ...   
12252  -2.015776  -1.966644   1.187858  -0.375836  -0.177199  -0.403895   
1346    1.109977   5.272019   1.249749   2.808767   5.170466  -6.267594   
11646  -0.808912   1.250632   0.506885  -1.418828  -3.539616  -0.049873   
15725   4.915212  -0.792421  -0.100772   4.403887   4.812652  -5.815247   
3582   -0.049259  -0.698291  -0.393727  -0.331023   1.694062  -0.560030   

             18        19        20         21        22         23  \
7374  -8.184188  1.339670 -2.650320   5.446167  6.565906   6.593064   
5428  -2.273136 -0.136379 -0.350567   2.753382 -1.266026  -1.341330   
2693  -0.530525  7.651406 -5.363283   0.852567 -0.311175   3.406032   
12345  0.214142 -7.941726 -0.514704  -4.148396  2.769721  -3.244688   
6225   2.169803 -1.273002  1.711290 -15.179893 -5.343740 -15.993336   
...         ...       ...       ...        ...       ...        ...   
12252 -0.640685 -0.721665  0.501587  -0.363929  0.798553  -1.886961   
1346   1.323211 -4.115852  2.077801  -9.006841 -8.827802   7.021431   
11646  0.995993  1.633953 -1.906225   0.835400 -2.062191   1.198091   
15725 -7.353508  3.612080  0.136487   2.945338  8.629677  -4.846002   
3582  -2.974892  0.121213  0.220461   0.369136 -1.455838  -1.887068   

              24         25         26         27         28         29  \
7374   -5.430837   0.905905  13.358457  -0.641665   0.748280  -2.976000   
5428    3.111043   1.194693  -3.292270   0.254575  -1.174591   0.480435   
2693   -0.218074   3.126443   9.160987  -2.840762  -1.936064 -11.259466   
12345  -5.299582  -5.271023   9.037873   7.288520   2.031449   0.145757   
6225   -1.742064   3.278709  -6.450616   3.512379  -0.694444   8.895505   
...          ...     

In [14]:
test = pd.concat([X_test, y_test],  ignore_index=True, axis = 1)
test

0           1          2          3          4          5    \
3416    0.189704   28.919616  10.533361  -7.927332   0.939890   1.211739   
15511  -3.106853   16.456593 -51.898294  -4.080210   5.370143   3.674215   
358   -18.604962  -27.935620  -2.691609   2.362909  -5.336133 -35.291964   
15967 -48.009839  143.476229  65.999959 -15.906573  14.380782  -0.519988   
3381   43.719272   71.439656  21.334669  -6.188984   3.181794  14.267478   
...          ...         ...        ...        ...        ...        ...   
14994 -14.183324   69.585348  32.609356  -3.750749   0.883306   0.031458   
15649   6.289888  -32.050495  87.843617   4.951944  -9.923721  16.940356   
1636  -52.526937  117.548782 -19.696015   9.568756 -21.686070   3.745054   
4581  -28.249098  -26.997105  54.082033   0.550082  -1.863535  -0.258588   
10215 -26.644633   42.590907 -24.583798   0.828119   2.140673   1.620500   

             6         7         8          9          10        11   \
3416    1.333441  2.564118 -6.411406   2.876855   0.956919  3.101259   
15511  -5.265217 -2.139120 -5.117588  10.340013   5.396825  2.345248   
358   -10.003569  9.441992  5.145907  -5.573095  -0.127377 -2.289430   
15967  -0.661647  0.508402 -0.389674   2.632044  -0.332601 -0.677930   
3381    9.211625 -2.142807  5.209670  -5.162856   1.323166  1.311630   
...          ...       ...       ...        ...        ...       ...   
14994  -0.639752  0.862550 -0.214938   1.032628  -0.194594 -0.607700   
15649   0.339763 -3.149450  8.660654  -0.037309   8.172703 -1.844126   
1636    2.493357  2.038464 -3.945271   3.929809   1.985667  0.674231   
4581    0.668584 -0.656412 -1.946633  -0.691243   0.201905 -0.066365   
10215  -0.330326  6.011797  6.592117  -0.954890 -13.776599 -8.848120   

            12         13         14         15         16        17   \
3416  -8.529234 -10.583074   1.932693  10.136539  -8.881020 -4.356402   
15511 -4.731179   3.715194   6.629870   1.749660   0.799742  2.181873   
358   -7.132261   3.044687   2.973517  -0.862779  -0.550246 -0.069629   
15967 -0.954025  -0.220590   1.159120  -0.038798  -0.510907  0.218608   
3381  -0.737458   8.526027  20.542059  -5.798982  -2.704614  4.019638   
...         ...        ...        ...        ...        ...       ...   
14994 -0.833191  -0.069196   0.332684  -0.116035  -0.117034  0.333213   
15649 -6.727844   1.379952  -1.525506  -1.715238   2.086551  2.428031   
1636  -4.529271   1.112313   2.443504  -0.393933   0.068022  1.684910   
4581  -0.306087   1.175810   0.228122  -0.438980   2.653260  1.390343   
10215  0.356365  -1.333549  -2.903368   7.527666  12.063146 -9.978130   

             18        19        20        21        22        23        24   \
3416    7.414614 -0.804898  2.149031  7.666741 -1.248036  2.837029  9.764282   
15511  -0.523960  6.647873 -2.261647 -6.332039  0.955492  0.860502 -7.772997   
358    -1.097204 -0.386541  0.296051  0.340816  1.588254  0.728344  1.311609   
15967   0.204927 -0.234617 -0.002591 -0.034558 -0.151341 -0.035863 -0.005164   
3381  -11.470925 -0.980102 -2.816019 -3.177117  4.505310 -4.087712 -1.039586   
...          ...       ...       ...       ...       ...       ...       ...   
14994   0.109178  0.044666  0.224984 -0.190616 -0.223395 -0.155622  0.089339   
15649  -0.347751  0.872738 -2.066843 -8.397568 -3.531681 -3.633328 -0.423106   
1636    1.034275  0.206830 -1.345586  0.378361  2.865062  2.412611  1.954568   
4581    2.351748 -1.443245  0.719894  0.481333  0.915609 -0.771436  1.976221   
10215   2.430197 -9.358362 -8.325772 -0.068952  1.464650  1.855198  5.490620   

             25        26        27        28        29        30        31   \
3416    6.431411  0.714642 -0.439375 -3.830394  2.527980  0.769800  1.357126   
15511  -2.515668 -4.242662  6.147079  5.774697 -1.870870 -1.086034  2.085153   
358    -0.693477 -0.368449 -0.055756  0.491074  0.155461  1.285336  0.896732   
15967   0.207313  0.162634  0.197082 -0.047215  0.007806 -0.098436 -0.116947 

In [15]:
test.columns = [*test.columns[:-1], 'stress']
test = pd.concat([test, id_test],  axis = 1)
test

0           1          2          3          4          5  \
3416    0.189704   28.919616  10.533361  -7.927332   0.939890   1.211739   
15511  -3.106853   16.456593 -51.898294  -4.080210   5.370143   3.674215   
358   -18.604962  -27.935620  -2.691609   2.362909  -5.336133 -35.291964   
15967 -48.009839  143.476229  65.999959 -15.906573  14.380782  -0.519988   
3381   43.719272   71.439656  21.334669  -6.188984   3.181794  14.267478   
...          ...         ...        ...        ...        ...        ...   
14994 -14.183324   69.585348  32.609356  -3.750749   0.883306   0.031458   
15649   6.289888  -32.050495  87.843617   4.951944  -9.923721  16.940356   
1636  -52.526937  117.548782 -19.696015   9.568756 -21.686070   3.745054   
4581  -28.249098  -26.997105  54.082033   0.550082  -1.863535  -0.258588   
10215 -26.644633   42.590907 -24.583798   0.828119   2.140673   1.620500   

               6         7         8          9         10        11  \
3416    1.333441  2.564118 -6.411406   2.876855   0.956919  3.101259   
15511  -5.265217 -2.139120 -5.117588  10.340013   5.396825  2.345248   
358   -10.003569  9.441992  5.145907  -5.573095  -0.127377 -2.289430   
15967  -0.661647  0.508402 -0.389674   2.632044  -0.332601 -0.677930   
3381    9.211625 -2.142807  5.209670  -5.162856   1.323166  1.311630   
...          ...       ...       ...        ...        ...       ...   
14994  -0.639752  0.862550 -0.214938   1.032628  -0.194594 -0.607700   
15649   0.339763 -3.149450  8.660654  -0.037309   8.172703 -1.844126   
1636    2.493357  2.038464 -3.945271   3.929809   1.985667  0.674231   
4581    0.668584 -0.656412 -1.946633  -0.691243   0.201905 -0.066365   
10215  -0.330326  6.011797  6.592117  -0.954890 -13.776599 -8.848120   

             12         13         14         15         16        17  \
3416  -8.529234 -10.583074   1.932693  10.136539  -8.881020 -4.356402   
15511 -4.731179   3.715194   6.629870   1.749660   0.799742  2.181873   
358   -7.132261   3.044687   2.973517  -0.862779  -0.550246 -0.069629   
15967 -0.954025  -0.220590   1.159120  -0.038798  -0.510907  0.218608   
3381  -0.737458   8.526027  20.542059  -5.798982  -2.704614  4.019638   
...         ...        ...        ...        ...        ...       ...   
14994 -0.833191  -0.069196   0.332684  -0.116035  -0.117034  0.333213   
15649 -6.727844   1.379952  -1.525506  -1.715238   2.086551  2.428031   
1636  -4.529271   1.112313   2.443504  -0.393933   0.068022  1.684910   
4581  -0.306087   1.175810   0.228122  -0.438980   2.653260  1.390343   
10215  0.356365  -1.333549  -2.903368   7.527666  12.063146 -9.978130   

              18        19        20        21        22        23        24  \
3416    7.414614 -0.804898  2.149031  7.666741 -1.248036  2.837029  9.764282   
15511  -0.523960  6.647873 -2.261647 -6.332039  0.955492  0.860502 -7.772997   
358    -1.097204 -0.386541  0.296051  0.340816  1.588254  0.728344  1.311609   
15967   0.204927 -0.234617 -0.002591 -0.034558 -0.151341 -0.035863 -0.005164   
3381  -11.470925 -0.980102 -2.816019 -3.177117  4.505310 -4.087712 -1.039586   
...          ...       ...       ...       ...       ...       ...       ...   
14994   0.109178  0.044666  0.224984 -0.190616 -0.223395 -0.155622  0.089339   
15649  -0.347751  0.872738 -2.066843 -8.397568 -3.531681 -3.633328 -0.423106   
1636    1.034275  0.206830 -1.345586  0.378361  2.865062  2.412611  1.954568   
4581    2.351748 -1.443245  0.719894  0.481333  0.915609 -0.771436  1.976221   
10215   2.430197 -9.358362 -8.325772 -0.068952  1.464650  1.855198  5.490620   

              25        26        27        28        29        30        31  \
3416    6.431411  0.714642 -0.439375 -3.830394  2.527980  0.769800  1.357126   
15511  -2.515668 -4.242662  6.147079  5.774697 -1.870870 -1.086034  2.085153   
358    -0.693477 -0.368449 -0.055756  0.491074  0.155461  1.285336  0.896732   
15967   0.207313  0.162634  0.197082 -0.047215  0.007806 -0.098436 -0.116947   

In [18]:
training

0          1          2          3          4          5  \
7374  -35.403967 -13.584755  11.910533  15.136094 -19.069353   4.406298   
5428   55.610077  31.351634  26.920716   6.137208 -21.156738   1.107372   
2693  -43.281369 -39.818919  32.249032   6.423005  -3.829736   4.179722   
12345 -75.210136  15.136503 -38.415731  -8.922326  -5.404721  27.737543   
6225  -35.006798  -9.199985 -15.419808  -2.743428   1.848794  31.206351   
...          ...        ...        ...        ...        ...        ...   
12252   0.045023  11.480156 -61.056940  10.162713 -10.111038   1.750809   
1346  -18.569692 -10.010034  -9.029104  -0.890967  -0.410305  -9.940186   
11646  -6.948346 -21.734892  47.836677   0.849393  -0.257242   4.994360   
15725 -73.976934  36.657368 -30.053970  -2.673558 -16.996494  14.263030   
3582  -38.876037 -16.368784  30.319440   2.665910  -7.007485  -0.832666   

               6          7          8         9         10         11  \
7374   39.507693 -14.858302   1.806010  0.578914  -6.761735 -10.927161   
5428   -0.616943   0.106355  -0.049682 -0.233233   0.386998  -0.835869   
2693   -1.178977   6.608860  -4.258251 -0.727822  -0.720481   2.712079   
12345  -0.152429  -3.538195  -8.038406 -1.110223  10.422630  -2.272864   
6225  -20.070332  19.967185 -18.206790 -2.159510 -26.930513   6.236844   
...          ...        ...        ...       ...        ...        ...   
12252   0.291299  -0.397514   0.238101  5.529392  -0.012417   4.954887   
1346   16.982668  -5.449044 -10.091026 -2.317217  -1.253335  -3.909347   
11646 -12.595930 -15.892247   8.285569  8.383630   1.287905  -7.678919   
15725   0.630004  -0.536571  -3.776405  1.725464  -4.255852   3.299784   
3582   -1.441021  -0.172129   0.248506 -1.231861  -1.289785  -0.805364   

              12         13         14         15         16         17  \
7374   10.178226   5.268345  18.744348   6.858127  -8.946382  -7.259109   
5428    0.043874  -0.121081  -1.106638   0.573177  -1.035813   1.245317   
2693   -1.521475   0.254781   0.243961  -3.569457   4.764510 -16.038955   
12345  -3.534238   4.808194  -0.618167  10.643919 -10.097375  -3.560674   
6225  -13.486625  13.091657  -1.850064   0.179548   2.903000   4.790746   
...          ...        ...        ...        ...        ...        ...   
12252  -2.015776  -1.966644   1.187858  -0.375836  -0.177199  -0.403895   
1346    1.109977   5.272019   1.249749   2.808767   5.170466  -6.267594   
11646  -0.808912   1.250632   0.506885  -1.418828  -3.539616  -0.049873   
15725   4.915212  -0.792421  -0.100772   4.403887   4.812652  -5.815247   
3582   -0.049259  -0.698291  -0.393727  -0.331023   1.694062  -0.560030   

             18        19        20         21        22         23  \
7374  -8.184188  1.339670 -2.650320   5.446167  6.565906   6.593064   
5428  -2.273136 -0.136379 -0.350567   2.753382 -1.266026  -1.341330   
2693  -0.530525  7.651406 -5.363283   0.852567 -0.311175   3.406032   
12345  0.214142 -7.941726 -0.514704  -4.148396  2.769721  -3.244688   
6225   2.169803 -1.273002  1.711290 -15.179893 -5.343740 -15.993336   
...         ...       ...       ...        ...       ...        ...   
12252 -0.640685 -0.721665  0.501587  -0.363929  0.798553  -1.886961   
1346   1.323211 -4.115852  2.077801  -9.006841 -8.827802   7.021431   
11646  0.995993  1.633953 -1.906225   0.835400 -2.062191   1.198091   
15725 -7.353508  3.612080  0.136487   2.945338  8.629677  -4.846002   
3582  -2.974892  0.121213  0.220461   0.369136 -1.455838  -1.887068   

              24         25         26         27         28         29  \
7374   -5.430837   0.905905  13.358457  -0.641665   0.748280  -2.976000   
5428    3.111043   1.194693  -3.292270   0.254575  -1.174591   0.480435   
2693   -0.218074   3.126443   9.160987  -2.840762  -1.936064 -11.259466   
12345  -5.299582  -5.271023   9.037873   7.288520   2.031449   0.145757   
6225   -1.742064   3.278709  -6.450616   3.512379  -0.694444   8.895505   
...          ...     

### SMOTE

In [19]:
import imblearn
from collections import Counter

counter = Counter(training["stress"])
print(counter)

X_train3 = training[training.columns.difference(['stress'])]
y_train3 = training["stress"]


oversample = SMOTE(sampling_strategy='auto')

X_res, y_res = oversample.fit_resample(X_train3, y_train3)

testX = pd.DataFrame(X_res)
testy = pd.DataFrame(y_res, columns=["stress"])
training2 = pd.concat([testX, testy], axis = 1)

counter = Counter(training2["stress"])
print(counter)

Counter({0.0: 11509, 1.0: 758})
Counter({0.0: 11509, 1.0: 11509})


In [21]:
training2["id"].value_counts()

10    2680
4     2476
1     2326
5     2312
7     2296
8     2227
3     2160
6     2000
9     1716
2     1549
0     1276
Name: id, dtype: int64

In [22]:
test

0           1          2          3          4          5  \
3416    0.189704   28.919616  10.533361  -7.927332   0.939890   1.211739   
15511  -3.106853   16.456593 -51.898294  -4.080210   5.370143   3.674215   
358   -18.604962  -27.935620  -2.691609   2.362909  -5.336133 -35.291964   
15967 -48.009839  143.476229  65.999959 -15.906573  14.380782  -0.519988   
3381   43.719272   71.439656  21.334669  -6.188984   3.181794  14.267478   
...          ...         ...        ...        ...        ...        ...   
14994 -14.183324   69.585348  32.609356  -3.750749   0.883306   0.031458   
15649   6.289888  -32.050495  87.843617   4.951944  -9.923721  16.940356   
1636  -52.526937  117.548782 -19.696015   9.568756 -21.686070   3.745054   
4581  -28.249098  -26.997105  54.082033   0.550082  -1.863535  -0.258588   
10215 -26.644633   42.590907 -24.583798   0.828119   2.140673   1.620500   

               6         7         8          9         10        11  \
3416    1.333441  2.564118 -6.411406   2.876855   0.956919  3.101259   
15511  -5.265217 -2.139120 -5.117588  10.340013   5.396825  2.345248   
358   -10.003569  9.441992  5.145907  -5.573095  -0.127377 -2.289430   
15967  -0.661647  0.508402 -0.389674   2.632044  -0.332601 -0.677930   
3381    9.211625 -2.142807  5.209670  -5.162856   1.323166  1.311630   
...          ...       ...       ...        ...        ...       ...   
14994  -0.639752  0.862550 -0.214938   1.032628  -0.194594 -0.607700   
15649   0.339763 -3.149450  8.660654  -0.037309   8.172703 -1.844126   
1636    2.493357  2.038464 -3.945271   3.929809   1.985667  0.674231   
4581    0.668584 -0.656412 -1.946633  -0.691243   0.201905 -0.066365   
10215  -0.330326  6.011797  6.592117  -0.954890 -13.776599 -8.848120   

             12         13         14         15         16        17  \
3416  -8.529234 -10.583074   1.932693  10.136539  -8.881020 -4.356402   
15511 -4.731179   3.715194   6.629870   1.749660   0.799742  2.181873   
358   -7.132261   3.044687   2.973517  -0.862779  -0.550246 -0.069629   
15967 -0.954025  -0.220590   1.159120  -0.038798  -0.510907  0.218608   
3381  -0.737458   8.526027  20.542059  -5.798982  -2.704614  4.019638   
...         ...        ...        ...        ...        ...       ...   
14994 -0.833191  -0.069196   0.332684  -0.116035  -0.117034  0.333213   
15649 -6.727844   1.379952  -1.525506  -1.715238   2.086551  2.428031   
1636  -4.529271   1.112313   2.443504  -0.393933   0.068022  1.684910   
4581  -0.306087   1.175810   0.228122  -0.438980   2.653260  1.390343   
10215  0.356365  -1.333549  -2.903368   7.527666  12.063146 -9.978130   

              18        19        20        21        22        23        24  \
3416    7.414614 -0.804898  2.149031  7.666741 -1.248036  2.837029  9.764282   
15511  -0.523960  6.647873 -2.261647 -6.332039  0.955492  0.860502 -7.772997   
358    -1.097204 -0.386541  0.296051  0.340816  1.588254  0.728344  1.311609   
15967   0.204927 -0.234617 -0.002591 -0.034558 -0.151341 -0.035863 -0.005164   
3381  -11.470925 -0.980102 -2.816019 -3.177117  4.505310 -4.087712 -1.039586   
...          ...       ...       ...       ...       ...       ...       ...   
14994   0.109178  0.044666  0.224984 -0.190616 -0.223395 -0.155622  0.089339   
15649  -0.347751  0.872738 -2.066843 -8.397568 -3.531681 -3.633328 -0.423106   
1636    1.034275  0.206830 -1.345586  0.378361  2.865062  2.412611  1.954568   
4581    2.351748 -1.443245  0.719894  0.481333  0.915609 -0.771436  1.976221   
10215   2.430197 -9.358362 -8.325772 -0.068952  1.464650  1.855198  5.490620   

              25        26        27        28        29        30        31  \
3416    6.431411  0.714642 -0.439375 -3.830394  2.527980  0.769800  1.357126   
15511  -2.515668 -4.242662  6.147079  5.774697 -1.870870 -1.086034  2.085153   
358    -0.693477 -0.368449 -0.055756  0.491074  0.155461  1.285336  0.896732   
15967   0.207313  0.162634  0.197082 -0.047215  0.007806 -0.098436 -0.116947   

In [23]:
X_train1 = training2[training2.columns.difference(['stress'])]
y_train1 = training2["stress"]

X_test = test[test.columns.difference(['stress'])]
y_test = test["stress"]


X_train, X_val, y_train, y_val = train_test_split(X_train1, y_train1, test_size=0.15, random_state=123)


In [24]:
X_train["dataset"] = 'Train'
X_val["dataset"] = 'Val'
X_test["dataset"] = 'Test'

In [25]:
training = pd.concat([X_train, y_train], axis = 1)
training

0          1          2         3         4          5  \
11782  20.513261  20.935081 -47.196465 -3.260985  4.507111   0.716637   
17858  92.417520 -21.996034  14.541838  1.649816 -5.103676  -2.204086   
12946 -33.102149 -25.279355  18.484651  5.258636 -3.633260  -1.777928   
641    35.193078 -47.192845 -18.580473  3.686088 -4.581467  -3.020590   
8266   44.319440  22.393429  48.325996 -0.647691 -0.581191  -1.557754   
...          ...        ...        ...       ...       ...        ...   
15377 -54.178521  -4.632872   4.158960 -3.990815  2.047251   3.504328   
21602  22.130392   2.785559 -31.086762 -0.630392 -2.863215  -2.961933   
17730  56.450132 -10.879024  75.455120  1.433016 -5.829393   2.824257   
15725 -75.052549  -0.780498  38.871810  0.313067 -1.657593  13.662887   
19966   7.253280   8.751163 -13.608670 -3.527743 -5.387027   6.875486   

               6         7          8          9         10        11  \
11782   0.303609 -0.124521   1.554185   0.872075  -1.211635  0.774948   
17858 -12.916046 -8.806577  20.147872   0.889388  13.900425 -1.695251   
12946   0.609462 -1.762000  -9.085495  -2.921152   7.843351 -1.065578   
641    -7.064863  1.519770  -8.749378   4.872315  -2.433733  2.658719   
8266  -18.945942  0.094177 -18.148259   9.633245  -0.760223 -4.055166   
...          ...       ...        ...        ...        ...       ...   
15377  -1.100544  0.128105  -1.014073   0.349285   1.152026  0.497959   
21602   1.175716  3.849455  -0.842921   2.986560  -0.257234 -0.844784   
17730  -1.479753 -2.310542  -2.469347  -2.274427  -1.022307 -1.704581   
15725 -12.417465  2.231190   2.472335   3.022012  -5.122452  5.360091   
19966   7.743169  1.689274  -8.357975  13.825284  16.892032 -7.508193   

              12         13         14        15        16        17  \
11782  -0.167665  -0.527095  -1.734244 -2.613306 -3.816877 -0.006163   
17858   2.033199   0.869391   5.352727  0.150905 -1.121834 -1.502346   
12946   1.009121   1.532083   1.277460 -1.847613  1.019588  4.833510   
641     5.638324   5.202803   0.948256  1.368559 -0.153309  0.159167   
8266   -0.690008  -2.115321  -0.085777  1.365274  1.606623  3.995087   
...          ...        ...        ...       ...       ...       ...   
15377   0.186366  -0.653400  -0.298931  0.189267 -0.478169 -4.203566   
21602   2.934086  -0.104387   2.822458  0.137255 -1.022689  1.236375   
17730   1.297631  -0.186464  -1.072385 -2.195732 -5.864875  0.701025   
15725  -1.521448  13.688011  -7.796515  0.955627  0.651470  2.987232   
19966  11.920217   9.263495 -11.365378 -1.110615 -9.783837  2.159680   

             18        19        20         21        22        23        24  \
11782 -5.440297  8.513212  3.392007  -4.255996 -2.457431  5.600076  7.823243   
17858  1.678052 -2.817253 -3.153518   3.158425  2.678990  0.655393  1.871454   
12946  2.539915 -2.744630  0.149898  -2.693646  1.109952  2.886398  0.117064   
641   -1.594899 -4.263516 -0.072834   1.418726 -0.743820  1.965298 -0.104084   
8266  -2.798103 -0.091903  0.786723   2.932066 -0.016289  5.282173 -1.828241   
...         ...       ...       ...        ...       ...       ...       ...   
15377 -2.127840 -1.220544 -2.799671   1.742041  1.029827 -0.399877  0.718607   
21602 -2.403708 -1.138282 -1.147329   0.142318 -1.048159  4.020632 -1.153686   
17730  1.461570 -8.932832 -2.723788   2.528093  3.603780 -1.601038  1.547651   
15725 -5.539724 -3.035007 -4.750402  -1.101296 -4.162165  0.291471  1.043135   
19966 -3.089823 -0.294881 -3.111444 -10.814975 -4.333356  2.763265 -5.935567   

             25        26        27        28         29        30        31  \
11782 -4.311128  3.535534 -1.741097 -1.677805  -5.388545  4.806354 -1.656096   
17858  1.883574  3.264242 -2.018841  0.965491   3.786294  3.979047  2.247135   
12946  1.862355  0.196216  0.157500 -1.216518  -0.585141  0.854058  0.480280   
641   -0.607058  2.691097  0.926544  0.850895  -0.251462  1.145015  0.108034   
8266   3.727883  2.127749 -5.075806

In [26]:
validation = pd.concat([X_val, y_val], axis = 1)
validation

0          1          2         3          4          5  \
11270 -27.244096 -24.212299  13.412595  4.149039  -7.756130  11.998854   
19688  23.970285  33.050571 -16.415358  5.236829  -7.593031   1.125960   
18881 -42.283778  49.179237 -46.279589 -0.635886  -4.112471  -0.162866   
8155  -21.268988  -4.133568  20.897463  0.764973  -6.732834   1.025748   
20581  98.104921  36.560280  43.685488 -3.417485   1.234487  -0.371585   
...          ...        ...        ...       ...        ...        ...   
4372   -3.369920  57.449353  38.246109 -1.370432 -17.889449 -17.916607   
1195   44.894246   1.047450   8.634897  0.692724 -19.332345   9.030531   
10557 -49.531832 -10.379031  -3.139591  1.049611  -2.082377  10.154315   
488     3.898473  63.951129 -63.021968  9.401708 -15.840341   0.162420   
19987  23.842643   8.008275 -33.412453 -0.354934  -2.381261  -0.673699   

               6          7         8          9         10         11  \
11270  18.781281  -3.885885  0.067465   1.028213  -6.244290  -4.641950   
19688 -14.091880   0.778238  6.742426   3.317004  -0.646434   2.689740   
18881  -0.000177   0.716935  0.415814   0.238952  -0.802692   0.219884   
8155   -3.333093  -1.181684 -0.352850  18.128061   6.315810 -19.333754   
20581  -0.338405   0.442146  0.333077   0.632280  -0.068159  -0.077362   
...          ...        ...       ...        ...        ...        ...   
4372   -3.852952  -4.459561 -0.308155  -2.623462  -8.202104  -7.322280   
1195   -8.546841  11.339530 -6.180951   0.715354 -16.597297   9.599698   
10557  -8.049121   1.809141 -2.245025 -15.511299 -20.410694   0.199431   
488     6.938922   1.306889 -1.138812   4.279176   1.094536   1.482111   
19987   1.381004   2.388470 -0.120447   2.549618  -1.179338   1.512319   

             12         13        14         15        16         17  \
11270  8.784783   7.364403  4.433576  -1.677470  0.520132 -10.878480   
19688 -0.176314  -2.915273  1.901881   3.381865  2.640432  -1.667495   
18881  0.114832  -0.114789  0.245828   2.550431 -1.915845  -1.614653   
8155  -5.612497  -0.211448 -1.570511  -2.902238 -0.115843   5.445059   
20581 -1.382828  -0.300435 -1.104523  -0.339933 -0.738553   1.667216   
...         ...        ...       ...        ...       ...        ...   
4372   6.162606   4.631907 -5.039856  12.851724  9.365384   0.235791   
1195   0.277891   4.247567 -7.959559  -0.197468  7.516103 -18.190476   
10557  1.737702  21.056742 -1.706327  -0.190170 -0.570742   0.872886   
488    1.831020  -0.447464 -0.262797  -1.754449  0.403284  -1.014654   
19987 -1.035621  -2.933921  0.455336  -1.225902 -1.452859   0.164406   

             18        19         20        21         22         23  \
11270 -5.806810  2.001759 -11.466633  9.867607   7.743125  13.415763   
19688 -1.371308 -0.349155   2.393477 -0.056667  -2.245682  -1.018497   
18881 -3.760670  0.319133  -0.161769  1.114861  -3.009618  -0.598076   
8155   1.397930  6.014067   0.262082 -4.010452  13.625893   4.976814   
20581  0.612360  0.120029  -0.347084 -0.328145  -1.606995   0.398225   
...         ...       ...        ...       ...        ...        ...   
4372   1.169009 -6.748745   3.567569 -1.813767  -6.767710   3.530975   
1195  -0.747469 -1.122263  -3.291223  7.771871  -2.602030  -6.608744   
10557  4.572999 -6.921841   1.633524 -2.541665  -5.131860   2.947553   
488   -0.062422  0.235041   1.963758 -1.641170  -1.641181   0.589143   
19987 -0.504156 -0.962702   0.230243 -1.187659  -0.843047   1.526150   

             24         25        26         27         28         29  \
11270 -8.799848   1.942146  1.097272   5.467409 -13.502771   0.780314   
19688 -1.650592  -4.298396  2.608871  -0.084752  -5.916964  -0.058565   
18881  0.211101   1.979723 -0.990944  -1.470122   0.206347  -2.857864   
8155  -6.302511  -8.754493  0.504030   1.234553  -5.712090  -0.441043   
20581 -0.258680   0.553306 -0.693920   0.076593   0.395972  -2.131545   
...         ...        ...       ...        ...        ...        ...

In [27]:
#X_test = pd.DataFrame(X_test)
test = pd.concat([X_test, y_test], axis = 1)
test

0           1          2          3          4          5  \
3416    0.189704   28.919616  10.533361  -7.927332   0.939890   1.211739   
15511  -3.106853   16.456593 -51.898294  -4.080210   5.370143   3.674215   
358   -18.604962  -27.935620  -2.691609   2.362909  -5.336133 -35.291964   
15967 -48.009839  143.476229  65.999959 -15.906573  14.380782  -0.519988   
3381   43.719272   71.439656  21.334669  -6.188984   3.181794  14.267478   
...          ...         ...        ...        ...        ...        ...   
14994 -14.183324   69.585348  32.609356  -3.750749   0.883306   0.031458   
15649   6.289888  -32.050495  87.843617   4.951944  -9.923721  16.940356   
1636  -52.526937  117.548782 -19.696015   9.568756 -21.686070   3.745054   
4581  -28.249098  -26.997105  54.082033   0.550082  -1.863535  -0.258588   
10215 -26.644633   42.590907 -24.583798   0.828119   2.140673   1.620500   

               6         7         8          9         10        11  \
3416    1.333441  2.564118 -6.411406   2.876855   0.956919  3.101259   
15511  -5.265217 -2.139120 -5.117588  10.340013   5.396825  2.345248   
358   -10.003569  9.441992  5.145907  -5.573095  -0.127377 -2.289430   
15967  -0.661647  0.508402 -0.389674   2.632044  -0.332601 -0.677930   
3381    9.211625 -2.142807  5.209670  -5.162856   1.323166  1.311630   
...          ...       ...       ...        ...        ...       ...   
14994  -0.639752  0.862550 -0.214938   1.032628  -0.194594 -0.607700   
15649   0.339763 -3.149450  8.660654  -0.037309   8.172703 -1.844126   
1636    2.493357  2.038464 -3.945271   3.929809   1.985667  0.674231   
4581    0.668584 -0.656412 -1.946633  -0.691243   0.201905 -0.066365   
10215  -0.330326  6.011797  6.592117  -0.954890 -13.776599 -8.848120   

             12         13         14         15         16        17  \
3416  -8.529234 -10.583074   1.932693  10.136539  -8.881020 -4.356402   
15511 -4.731179   3.715194   6.629870   1.749660   0.799742  2.181873   
358   -7.132261   3.044687   2.973517  -0.862779  -0.550246 -0.069629   
15967 -0.954025  -0.220590   1.159120  -0.038798  -0.510907  0.218608   
3381  -0.737458   8.526027  20.542059  -5.798982  -2.704614  4.019638   
...         ...        ...        ...        ...        ...       ...   
14994 -0.833191  -0.069196   0.332684  -0.116035  -0.117034  0.333213   
15649 -6.727844   1.379952  -1.525506  -1.715238   2.086551  2.428031   
1636  -4.529271   1.112313   2.443504  -0.393933   0.068022  1.684910   
4581  -0.306087   1.175810   0.228122  -0.438980   2.653260  1.390343   
10215  0.356365  -1.333549  -2.903368   7.527666  12.063146 -9.978130   

              18        19        20        21        22        23        24  \
3416    7.414614 -0.804898  2.149031  7.666741 -1.248036  2.837029  9.764282   
15511  -0.523960  6.647873 -2.261647 -6.332039  0.955492  0.860502 -7.772997   
358    -1.097204 -0.386541  0.296051  0.340816  1.588254  0.728344  1.311609   
15967   0.204927 -0.234617 -0.002591 -0.034558 -0.151341 -0.035863 -0.005164   
3381  -11.470925 -0.980102 -2.816019 -3.177117  4.505310 -4.087712 -1.039586   
...          ...       ...       ...       ...       ...       ...       ...   
14994   0.109178  0.044666  0.224984 -0.190616 -0.223395 -0.155622  0.089339   
15649  -0.347751  0.872738 -2.066843 -8.397568 -3.531681 -3.633328 -0.423106   
1636    1.034275  0.206830 -1.345586  0.378361  2.865062  2.412611  1.954568   
4581    2.351748 -1.443245  0.719894  0.481333  0.915609 -0.771436  1.976221   
10215   2.430197 -9.358362 -8.325772 -0.068952  1.464650  1.855198  5.490620   

              25        26        27        28        29        30        31  \
3416    6.431411  0.714642 -0.439375 -3.830394  2.527980  0.769800  1.357126   
15511  -2.515668 -4.242662  6.147079  5.774697 -1.870870 -1.086034  2.085153   
358    -0.693477 -0.368449 -0.055756  0.491074  0.155461  1.285336  0.896732   
15967   0.207313  0.162634  0.197082 -0.047215  0.007806 -0.098436 -0.116947   

In [28]:
adarp = pd.concat([training, validation, test])
adarp

0           1          2         3          4          5  \
11782  20.513261   20.935081 -47.196465 -3.260985   4.507111   0.716637   
17858  92.417520  -21.996034  14.541838  1.649816  -5.103676  -2.204086   
12946 -33.102149  -25.279355  18.484651  5.258636  -3.633260  -1.777928   
641    35.193078  -47.192845 -18.580473  3.686088  -4.581467  -3.020590   
8266   44.319440   22.393429  48.325996 -0.647691  -0.581191  -1.557754   
...          ...         ...        ...       ...        ...        ...   
14994 -14.183324   69.585348  32.609356 -3.750749   0.883306   0.031458   
15649   6.289888  -32.050495  87.843617  4.951944  -9.923721  16.940356   
1636  -52.526937  117.548782 -19.696015  9.568756 -21.686070   3.745054   
4581  -28.249098  -26.997105  54.082033  0.550082  -1.863535  -0.258588   
10215 -26.644633   42.590907 -24.583798  0.828119   2.140673   1.620500   

               6         7          8         9         10        11  \
11782   0.303609 -0.124521   1.554185  0.872075  -1.211635  0.774948   
17858 -12.916046 -8.806577  20.147872  0.889388  13.900425 -1.695251   
12946   0.609462 -1.762000  -9.085495 -2.921152   7.843351 -1.065578   
641    -7.064863  1.519770  -8.749378  4.872315  -2.433733  2.658719   
8266  -18.945942  0.094177 -18.148259  9.633245  -0.760223 -4.055166   
...          ...       ...        ...       ...        ...       ...   
14994  -0.639752  0.862550  -0.214938  1.032628  -0.194594 -0.607700   
15649   0.339763 -3.149450   8.660654 -0.037309   8.172703 -1.844126   
1636    2.493357  2.038464  -3.945271  3.929809   1.985667  0.674231   
4581    0.668584 -0.656412  -1.946633 -0.691243   0.201905 -0.066365   
10215  -0.330326  6.011797   6.592117 -0.954890 -13.776599 -8.848120   

             12        13        14        15         16        17        18  \
11782 -0.167665 -0.527095 -1.734244 -2.613306  -3.816877 -0.006163 -5.440297   
17858  2.033199  0.869391  5.352727  0.150905  -1.121834 -1.502346  1.678052   
12946  1.009121  1.532083  1.277460 -1.847613   1.019588  4.833510  2.539915   
641    5.638324  5.202803  0.948256  1.368559  -0.153309  0.159167 -1.594899   
8266  -0.690008 -2.115321 -0.085777  1.365274   1.606623  3.995087 -2.798103   
...         ...       ...       ...       ...        ...       ...       ...   
14994 -0.833191 -0.069196  0.332684 -0.116035  -0.117034  0.333213  0.109178   
15649 -6.727844  1.379952 -1.525506 -1.715238   2.086551  2.428031 -0.347751   
1636  -4.529271  1.112313  2.443504 -0.393933   0.068022  1.684910  1.034275   
4581  -0.306087  1.175810  0.228122 -0.438980   2.653260  1.390343  2.351748   
10215  0.356365 -1.333549 -2.903368  7.527666  12.063146 -9.978130  2.430197   

             19        20        21        22        23        24         25  \
11782  8.513212  3.392007 -4.255996 -2.457431  5.600076  7.823243  -4.311128   
17858 -2.817253 -3.153518  3.158425  2.678990  0.655393  1.871454   1.883574   
12946 -2.744630  0.149898 -2.693646  1.109952  2.886398  0.117064   1.862355   
641   -4.263516 -0.072834  1.418726 -0.743820  1.965298 -0.104084  -0.607058   
8266  -0.091903  0.786723  2.932066 -0.016289  5.282173 -1.828241   3.727883   
...         ...       ...       ...       ...       ...       ...        ...   
14994  0.044666  0.224984 -0.190616 -0.223395 -0.155622  0.089339   1.222451   
15649  0.872738 -2.066843 -8.397568 -3.531681 -3.633328 -0.423106   6.410680   
1636   0.206830 -1.345586  0.378361  2.865062  2.412611  1.954568  -0.612624   
4581  -1.443245  0.719894  0.481333  0.915609 -0.771436  1.976221   0.449564   
10215 -9.358362 -8.325772 -0.068952  1.464650  1.855198  5.490620  10.775444   

             26        27        28        29        30        31        32  \
11782  3.535534 -1.741097 -1.677805 -5.388545  4.806354 -1.656096 -3.743774   
17858  3.264242 -2.018841  0.965491  3.786294  3.979047  2.247135 -2.952497   
12946  0.196216  0.157500 -1.216518 -0.585141  0.854058  0.480280  0.538696   
641    2.69

In [29]:
adarp.to_csv("Final_CSVs/adarp_new.csv", index = False)

## User-based Models

In [12]:
unique_participants2 = adarp_dataset["id"].unique()

In [14]:
person_group2 = adarp_dataset.groupby('id')

In [15]:
accuracies_adarp = []
precision_adarp = []
recall_adarp = []
f1scores_adarp = []

for participant in unique_participants2:
    print("Participant: ",participant)
    part_df = person_group2.get_group(participant)
    grid = setup(data=part_df, target='stress', pca = True, pca_components = 200, fix_imbalance = True, html=False, silent=True, verbose=False) #fix_imbalance = True,
    best = compare_models(sort='F1')
    accuracies_adarp.append(pull()['Accuracy'][0])
    precision_adarp.append(pull()['Prec.'][0])
    recall_adarp.append(pull()['Recall'][0])
    f1scores_adarp.append(pull()['F1'][0])
    print(best)

Participant:  8


Model  Accuracy     AUC  Recall   Prec.     F1   Kappa  \
lr  Logistic Regression    0.6806  0.5478  0.3762  0.0766  0.127  0.0292   

       MCC  TT (Sec)  
lr  0.0412     0.673

Model  Accuracy     AUC  Recall   Prec.     F1   Kappa  \
knn  K Neighbors Classifier    0.6617  0.6106  0.4524  0.0854  0.143  0.0459   
lr      Logistic Regression    0.6806  0.5478  0.3762  0.0766  0.127  0.0292   

        MCC  TT (Sec)  
knn  0.0675     0.248  
lr   0.0412     0.673

Model  Accuracy     AUC  Recall   Prec.      F1   Kappa  \
knn  K Neighbors Classifier    0.6617  0.6106  0.4524  0.0854  0.1430  0.0459   
lr      Logistic Regression    0.6806  0.5478  0.3762  0.0766  0.1270  0.0292   
nb              Naive Bayes    0.4285  0.4950  0.6071  0.0635  0.1149  0.0060   

        MCC  TT (Sec)  
knn  0.0675     0.248  
lr   0.0412     0.673  
nb   0.0109     0.010

Model  Accuracy     AUC  Recall   Prec.      F1  \
knn    K Neighbors Classifier    0.6617  0.6106  0.4524  0.0854  0.1430   
dt   Decision Tree Classifier    0.8205  0.5436  0.2286  0.0973  0.1350   
lr        Logistic Regression    0.6806  0.5478  0.3762  0.0766  0.1270   
nb                Naive Bayes    0.4285  0.4950  0.6071  0.0635  0.1149   

      Kappa     MCC  TT (Sec)  
knn  0.0459  0.0675     0.248  
dt   0.0549  0.0607     0.042  
lr   0.0292  0.0412     0.673  
nb   0.0060  0.0109     0.010

...

Model  Accuracy     AUC  Recall   Prec.  \
ridge                 Ridge Classifier    0.8389  0.0000  0.3083  0.0461   
lda       Linear Discriminant Analysis    0.8389  0.6583  0.3083  0.0461   
lr                 Logistic Regression    0.8359  0.5855  0.2750  0.0447   
knn             K Neighbors Classifier    0.8048  0.6250  0.2750  0.0341   
svm                SVM - Linear Kernel    0.4685  0.0000  0.6333  0.0279   
nb                         Naive Bayes    0.4758  0.3633  0.3167  0.0144   
dt            Decision Tree Classifier    0.9086  0.4813  0.0333  0.0200   
ada               Ada Boost Classifier    0.9287  0.5218  0.0333  0.0100   
rf            Random Forest Classifier    0.9770  0.5049  0.0000  0.0000   
qda    Quadratic Discriminant Analysis    0.9770  0.5000  0.0000  0.0000   
gbc       Gradient Boosting Classifier    0.9703  0.4628  0.0000  0.0000   
et              Extra Trees Classifier    0.9770  0.5698  0.0000  0.0000   

           F1   Kappa     MCC  TT (Sec)  
ridge  0.0801  0.0420  0.0665     0.024  
lda    0.0801  0.0420  0.0665     0.046  
lr     0.0765  0.0383  0.0559     0.892  
knn    0.0605  0.0207  0.0360     0.304  
svm    0.0533  0.0097  0.0314     0.047  
nb     0.0276 -0.0172 -0.0606     0.024  
dt     0.0250 -0.0086 -0.0145     0.087  
ada    0.0154 -0.0145 -0.0149     0.308  
rf     0.0000  0.0000  0.0000     0.198  
qda    0.0000  0.0000  0.0000     0.036  
gbc    0.0000 -0.0086 -0.0094     1.347  
et     0.0000  0.0000  0.0000     0.092

Model  Accuracy     AUC  Recall   Prec.  \
ridge                    Ridge Classifier    0.8389  0.0000  0.3083  0.0461   
lda          Linear Discriminant Analysis    0.8389  0.6583  0.3083  0.0461   
lr                    Logistic Regression    0.8359  0.5855  0.2750  0.0447   
knn                K Neighbors Classifier    0.8048  0.6250  0.2750  0.0341   
svm                   SVM - Linear Kernel    0.4685  0.0000  0.6333  0.0279   
nb                            Naive Bayes    0.4758  0.3633  0.3167  0.0144   
dt               Decision Tree Classifier    0.9086  0.4813  0.0333  0.0200   
ada                  Ada Boost Classifier    0.9287  0.5218  0.0333  0.0100   
rf               Random Forest Classifier    0.9770  0.5049  0.0000  0.0000   
qda       Quadratic Discriminant Analysis    0.9770  0.5000  0.0000  0.0000   
gbc          Gradient Boosting Classifier    0.9703  0.4628  0.0000  0.0000   
et                 Extra Trees Classifier    0.9770  0.5698  0.0000  0.0000   
lightgbm  Light Gradient Boosting Machine    0.9755  0.4514  0.0000  0.0000   

              F1   Kappa     MCC  TT (Sec)  
ridge     0.0801  0.0420  0.0665     0.024  
lda       0.0801  0.0420  0.0665     0.046  
lr        0.0765  0.0383  0.0559     0.892  
knn       0.0605  0.0207  0.0360     0.304  
svm       0.0533  0.0097  0.0314     0.047  
nb        0.0276 -0.0172 -0.0606     0.024  
dt        0.0250 -0.0086 -0.0145     0.087  
ada       0.0154 -0.0145 -0.0149     0.308  
rf        0.0000  0.0000  0.0000     0.198  
qda       0.0000  0.0000  0.0000     0.036  
gbc       0.0000 -0.0086 -0.0094     1.347  
et        0.0000  0.0000  0.0000     0.092  
lightgbm  0.0000 -0.0023 -0.0026     0.769

Model  Accuracy     AUC  Recall   Prec.  \
ridge                    Ridge Classifier    0.8389  0.0000  0.3083  0.0461   
lda          Linear Discriminant Analysis    0.8389  0.6583  0.3083  0.0461   
lr                    Logistic Regression    0.8359  0.5855  0.2750  0.0447   
knn                K Neighbors Classifier    0.8048  0.6250  0.2750  0.0341   
svm                   SVM - Linear Kernel    0.4685  0.0000  0.6333  0.0279   
nb                            Naive Bayes    0.4758  0.3633  0.3167  0.0144   
dt               Decision Tree Classifier    0.9086  0.4813  0.0333  0.0200   
ada                  Ada Boost Classifier    0.9287  0.5218  0.0333  0.0100   
rf               Random Forest Classifier    0.9770  0.5049  0.0000  0.0000   
qda       Quadratic Discriminant Analysis    0.9770  0.5000  0.0000  0.0000   
gbc          Gradient Boosting Classifier    0.9703  0.4628  0.0000  0.0000   
et                 Extra Trees Classifier    0.9770  0.5698  0.0000  0.0000   
lightgbm  Light Gradient Boosting Machine    0.9755  0.4514  0.0000  0.0000   
dummy                    Dummy Classifier    0.9770  0.5000  0.0000  0.0000   

              F1   Kappa     MCC  TT (Sec)  
ridge     0.0801  0.0420  0.0665     0.024  
lda       0.0801  0.0420  0.0665     0.046  
lr        0.0765  0.0383  0.0559     0.892  
knn       0.0605  0.0207  0.0360     0.304  
svm       0.0533  0.0097  0.0314     0.047  
nb        0.0276 -0.0172 -0.0606     0.024  
dt        0.0250 -0.0086 -0.0145     0.087  
ada       0.0154 -0.0145 -0.0149     0.308  
rf        0.0000  0.0000  0.0000     0.198  
qda       0.0000  0.0000  0.0000     0.036  
gbc       0.0000 -0.0086 -0.0094     1.347  
et        0.0000  0.0000  0.0000     0.092  
lightgbm  0.0000 -0.0023 -0.0026     0.769  
dummy     0.0000  0.0000  0.0000     0.019

Model  Accuracy     AUC  Recall   Prec.  \
ridge                    Ridge Classifier    0.8389  0.0000  0.3083  0.0461   
lda          Linear Discriminant Analysis    0.8389  0.6583  0.3083  0.0461   
lr                    Logistic Regression    0.8359  0.5855  0.2750  0.0447   
knn                K Neighbors Classifier    0.8048  0.6250  0.2750  0.0341   
svm                   SVM - Linear Kernel    0.4685  0.0000  0.6333  0.0279   
nb                            Naive Bayes    0.4758  0.3633  0.3167  0.0144   
dt               Decision Tree Classifier    0.9086  0.4813  0.0333  0.0200   
ada                  Ada Boost Classifier    0.9287  0.5218  0.0333  0.0100   
rf               Random Forest Classifier    0.9770  0.5049  0.0000  0.0000   
qda       Quadratic Discriminant Analysis    0.9770  0.5000  0.0000  0.0000   
gbc          Gradient Boosting Classifier    0.9703  0.4628  0.0000  0.0000   
et                 Extra Trees Classifier    0.9770  0.5698  0.0000  0.0000   
lightgbm  Light Gradient Boosting Machine    0.9755  0.4514  0.0000  0.0000   
dummy                    Dummy Classifier    0.9770  0.5000  0.0000  0.0000   

              F1   Kappa     MCC  TT (Sec)  
ridge     0.0801  0.0420  0.0665     0.024  
lda       0.0801  0.0420  0.0665     0.046  
lr        0.0765  0.0383  0.0559     0.892  
knn       0.0605  0.0207  0.0360     0.304  
svm       0.0533  0.0097  0.0314     0.047  
nb        0.0276 -0.0172 -0.0606     0.024  
dt        0.0250 -0.0086 -0.0145     0.087  
ada       0.0154 -0.0145 -0.0149     0.308  
rf        0.0000  0.0000  0.0000     0.198  
qda       0.0000  0.0000  0.0000     0.036  
gbc       0.0000 -0.0086 -0.0094     1.347  
et        0.0000  0.0000  0.0000     0.092  
lightgbm  0.0000 -0.0023 -0.0026     0.769  
dummy     0.0000  0.0000  0.0000     0.019

RidgeClassifier(alpha=1.0, class_weight=None, copy_X=True, fit_intercept=True,
                max_iter=None, normalize=False, random_state=7687,
                solver='auto', tol=0.001)


In [16]:
mean_acc_adarp = statistics.mean(accuracies_adarp)
mean_prec_adarp = statistics.mean(precision_adarp)
mean_rec_adarp = statistics.mean(recall_adarp)
mean_f1_adarp = statistics.mean(f1scores_adarp)
std_acc_adarp = statistics.stdev(accuracies_adarp)
std_prec_adarp = statistics.stdev(precision_adarp)
std_rec_adarp = statistics.stdev(recall_adarp)
std_f1_adarp = statistics.stdev(f1scores_adarp)

In [17]:
print("Mean Accuracy ADARP: ",mean_acc_adarp)
print("Mean Precision ADARP: ",mean_prec_adarp)
print("Mean Recall ADARP: ",mean_rec_adarp)
print("Mean F1-score ADARP: ",mean_f1_adarp)
print("Standard deviation of Accuracy ADARP: ",std_acc_adarp)
print("Standard deviation of Precision ADARP: ",std_prec_adarp)
print("Standard deviation of Recall ADARP: ",std_rec_adarp)
print("Standard deviation of F1-score ADARP: ",std_f1_adarp)

Mean Accuracy ADARP:  0.7903454545454546
Mean Precision ADARP:  0.13390909090909092
Mean Recall ADARP:  0.3529909090909091
Mean F1-score ADARP:  0.17027272727272727
Standard deviation of Accuracy ADARP:  0.12412676072174253
Standard deviation of Precision ADARP:  0.08094069995429314
Standard deviation of Recall ADARP:  0.20341186029602826
Standard deviation of F1-score ADARP:  0.10494063170106317


# LIFESNAPS

In [11]:
lifesnaps = pd.read_csv('Final_CSVs/lifesnaps_time.csv')

In [2]:
lifesnaps = pd.read_csv('Final_CSVs/lifesnaps_new.csv')

In [3]:
lifesnaps['id']

0       621e329067b776a2402ffad2
1       621e2f1b67b776a240b3d87c
2       621e339967b776a240e502de
3       621e332267b776a24092a584
4       621e32d967b776a240627414
                  ...           
7405    621e346f67b776a24081744f
7406    621e34ec67b776a240d60873
7407    621e309267b776a240ae1cdb
7408    621e32d967b776a240627414
7409    621e360b67b776a24039709f
Name: id, Length: 7410, dtype: object

In [9]:
unique_participants4 = lifesnaps["id"].unique()

In [10]:
len(unique_participants4)

14

In [8]:
for participant in range(0, 70, 5):
    print("Participant: ",participant)

    if(participant == 65):
        for part in range(participant+1, participant+6):
            lifesnaps['id'] = np.where(lifesnaps['id']==unique_participants3[part],unique_participants3[participant],lifesnaps['id'])
    
    else:
        for part in range(participant+1, participant+5):
            lifesnaps['id'] = np.where(lifesnaps['id']==unique_participants3[part],unique_participants3[participant],lifesnaps['id'])



Participant:  0
Participant:  5
Participant:  10
Participant:  15
Participant:  20
Participant:  25
Participant:  30
Participant:  35
Participant:  40
Participant:  45
Participant:  50
Participant:  55
Participant:  60
Participant:  65


In [6]:
person_group3 = lifesnaps.groupby('id')

In [15]:
lifesnaps = lifesnaps.rename(columns={"labels": "stress"})

In [16]:
X = lifesnaps[lifesnaps.columns.difference(['stress'])]
y = lifesnaps["stress"]

X_train1, X_test, y_train1, y_test = train_test_split(X, y, test_size=0.25, random_state=123)
X_train, X_val, y_train, y_val = train_test_split(X_train1, y_train1, test_size=0.15, random_state=123)

X_train["dataset"] = 'Train'
X_val["dataset"] = 'Val'
X_test["dataset"] = 'Test'

In [17]:
training = pd.concat([X_train, y_train], axis = 1)
validation = pd.concat([X_val, y_val], axis = 1)
test = pd.concat([X_test, y_test], axis = 1)

In [18]:
lifesnaps = pd.concat([training, validation, test])

In [4]:
lifesnaps

ENTERTAINMENT  GYM  HOME  HOME1OFFICE  OTHER  OUTDOORS  TRANSIT  \
0               0.0  0.0   1.0          0.0    0.0       0.0      0.0   
1               NaN  NaN   NaN          NaN    NaN       NaN      NaN   
2               NaN  NaN   NaN          NaN    NaN       NaN      NaN   
3               NaN  NaN   NaN          NaN    NaN       NaN      NaN   
4               NaN  NaN   NaN          NaN    NaN       NaN      NaN   
...             ...  ...   ...          ...    ...       ...      ...   
7405            NaN  NaN   NaN          NaN    NaN       NaN      NaN   
7406            NaN  NaN   NaN          NaN    NaN       NaN      NaN   
7407            NaN  NaN   NaN          NaN    NaN       NaN      NaN   
7408            NaN  NaN   NaN          NaN    NaN       NaN      NaN   
7409            NaN  NaN   NaN          NaN    NaN       NaN      NaN   

      WORK/SCHOOL  age   bmi        bpm  calories  \
0             1.0  1.0  23.0  91.659123   3241.52   
1             NaN  1.0  22.0        NaN       NaN   
2             NaN  0.0  20.0  90.021444   2523.09   
3             NaN  0.0  21.0        NaN   1800.00   
4             NaN  1.0  30.0        NaN   2318.40   
...           ...  ...   ...        ...       ...   
7405          NaN  NaN   NaN  82.571340   1429.29   
7406          NaN  0.0  24.0        NaN   1612.80   
7407          NaN  0.0  18.0        NaN   1713.60   
7408          NaN  1.0  30.0        NaN   2318.40   
7409          NaN  1.0  18.0  75.570213   1759.72   

      daily1temperature1variation  day   day1cos   day1sin  distance  \
0                       -0.460087    4  0.688967  0.724793    9275.7   
1                             NaN   12 -0.758758  0.651372       NaN   
2                       -1.986618   18 -0.874347 -0.485302    6187.5   
3                             NaN    3  0.820763  0.571268       NaN   
4                             NaN    3  0.820763  0.571268       NaN   
...                           ...  ...       ...       ...       ...   
7405                          NaN   15 -0.994869  0.101168    1723.5   
7406                          NaN   13 -0.874347  0.485302       NaN   
7407                          NaN   24  0.151428 -0.988468       NaN   
7408                          NaN   13 -0.874347  0.485302       NaN   
7409                    -2.080849   27  0.688967 -0.724793    6701.5   

      filteredDemographicVO2Max  full1sleep1breathing1rate  gender  \
0                      48.07785                        NaN     0.0   
1                           NaN                        NaN     1.0   
2                      49.72347                       11.6     1.0   
3                           NaN                        NaN     0.0   
4                           NaN                        NaN     0.0   
...                         ...                        ...     ...   
7405                   36.39159                        NaN     NaN   
7406                        NaN                        NaN     0.0   
7407                        NaN                        NaN     0.0   
7408                        NaN                        NaN     0.0   
7409                   45.77456                       15.6     1.0   

                            id  lightly1active1minutes  max1goal  min1goal  \
0     621e329067b776a2402ffad2                   376.0   10000.0    8000.0   
1     621e2f1b67b776a240b3d87c                     NaN       NaN       NaN   
2     621e339967b776a240e502de                   256.0       NaN       NaN   
3     621e332267b776a24092a584                     0.0       NaN       NaN   
4     621e32d967b776a240627414                     0.0       NaN       NaN   
...                        ...                     ...       ...       ...   
7405  621e346f67b776a24081744f                    30.0       NaN       NaN   
7406  621e34ec67b776a240d60873                     0.0       NaN       NaN   
7407  621e309267b776a240ae1cdb                     0.0       NaN       NaN   
7408  

In [70]:
for i in lifesnaps.columns:
    if isinstance(lifesnaps[i][0], (str)):
        print(i)

id
dataset


In [73]:
lifesnaps["badgeType"].value_counts()

['LIFETIME_DISTANCE']                                                      128
['DAILY_STEPS']                                                            111
['DAILY_FLOORS', 'DAILY_STEPS']                                             83
['LIFETIME_FLOORS']                                                         77
['DAILY_FLOORS']                                                            75
['LIFETIME_FLOORS', 'LIFETIME_DISTANCE']                                    14
['LIFETIME_FLOORS', 'DAILY_STEPS']                                           7
['LIFETIME_WEIGHT_GOAL_SETUP']                                               4
['DAILY_FLOORS', 'LIFETIME_DISTANCE', 'DAILY_STEPS']                         4
['LIFETIME_FLOORS', 'DAILY_FLOORS', 'DAILY_STEPS']                           3
['LIFETIME_FLOORS', 'DAILY_FLOORS']                                          3
['LIFETIME_DISTANCE', 'DAILY_STEPS']                                         2
['GOAL_BASED_WEIGHT_LOSS', 'DAILY_STEPS']           

In [61]:
lifesnaps["age"].value_counts()
lifesnaps['age'] = np.where(lifesnaps['age']=='<30',0,lifesnaps['age'])
lifesnaps['age'] = np.where(lifesnaps['age']=='>=30',1,lifesnaps['age'])


In [65]:
lifesnaps["gender"].value_counts()
lifesnaps['gender'] = np.where(lifesnaps['gender']=='MALE',0,lifesnaps['gender'])
lifesnaps['gender'] = np.where(lifesnaps['gender']=='FEMALE',1,lifesnaps['gender'])

In [69]:
lifesnaps["bmi"].value_counts()
lifesnaps['bmi'] = np.where(lifesnaps['bmi']=='<19',18.0,lifesnaps['bmi'])
lifesnaps['bmi'] = np.where(lifesnaps['bmi']=='>=30',30.0,lifesnaps['bmi'])
lifesnaps['bmi'] = np.where(lifesnaps['bmi']=='>=25',25.0,lifesnaps['bmi'])

#lifesnaps['gender'] = np.where(lifesnaps['gender']=='FEMALE',1,lifesnaps['gender'])

In [55]:
lifesnaps.drop(['activityType'], axis=1, inplace=True)

In [75]:
lifesnaps.drop(['badgeType'], axis=1, inplace=True)

In [26]:
for col in lifesnaps.columns:
    new_col = col.replace("_","1")
    lifesnaps = lifesnaps.rename(columns={col: new_col})

In [56]:
lifesnaps.columns

Index(['ENTERTAINMENT', 'GYM', 'HOME', 'HOME1OFFICE', 'OTHER', 'OUTDOORS',
       'TRANSIT', 'WORK/SCHOOL', 'age', 'badgeType', 'bmi', 'bpm', 'calories',
       'daily1temperature1variation', 'day', 'day1cos', 'day1sin', 'distance',
       'filteredDemographicVO2Max', 'full1sleep1breathing1rate', 'gender',
       'id', 'lightly1active1minutes', 'max1goal', 'min1goal',
       'mindfulness1session', 'minutesAfterWakeup', 'minutesAsleep',
       'minutesAwake', 'minutesToFallAsleep', 'minutes1below1default1zone11',
       'minutes1in1default1zone11', 'minutes1in1default1zone12',
       'minutes1in1default1zone13', 'moderately1active1minutes', 'month',
       'month1cos', 'month1sin', 'nightly1temperature', 'nremhr', 'resting1hr',
       'rmssd', 'scl1avg', 'sedentary1minutes', 'sleep1deep1ratio',
       'sleep1duration', 'sleep1efficiency', 'sleep1light1ratio',
       'sleep1rem1ratio', 'sleep1wake1ratio', 'spo2', 'step1goal',
       'step1goal1label', 'steps', 'very1active1minutes', 'wee

In [11]:
lifesnaps.to_csv("Final_CSVs/lifesnaps_new_gr.csv", index = False)

In [85]:
lifesnaps['step1goal'] = np.where(lifesnaps['step1goal']=='NO_GOAL',0,lifesnaps['step1goal'])

lifesnaps['step1goal'].value_counts()

7999     602
9999     362
4999     310
0        245
14999    200
2000     139
19999     44
24999     10
25000      1
Name: step1goal, dtype: int64

In [84]:
lifesnaps["step1goal1label"].value_counts()

3    602
4    362
2    310
0    247
5    200
1    139
6     44
7     10
8      1
Name: step1goal1label, dtype: int64

In [83]:
lifesnaps["step1goal1label"].value_counts()
lifesnaps['step1goal1label'] = np.where(lifesnaps['step1goal1label']=='No Goal',0,lifesnaps['step1goal1label'])
lifesnaps['step1goal1label'] = np.where(lifesnaps['step1goal1label']=='Less than 2000',1,lifesnaps['step1goal1label'])
lifesnaps['step1goal1label'] = np.where(lifesnaps['step1goal1label']=='2000-4999',2,lifesnaps['step1goal1label'])
lifesnaps['step1goal1label'] = np.where(lifesnaps['step1goal1label']=='5000-7999',3,lifesnaps['step1goal1label'])
lifesnaps['step1goal1label'] = np.where(lifesnaps['step1goal1label']=='8000-9999',4,lifesnaps['step1goal1label'])
lifesnaps['step1goal1label'] = np.where(lifesnaps['step1goal1label']=='10000-14999',5,lifesnaps['step1goal1label'])
lifesnaps['step1goal1label'] = np.where(lifesnaps['step1goal1label']=='15000-19999',6,lifesnaps['step1goal1label'])
lifesnaps['step1goal1label'] = np.where(lifesnaps['step1goal1label']=='20000-24999',7,lifesnaps['step1goal1label'])
lifesnaps['step1goal1label'] = np.where(lifesnaps['step1goal1label']=='More than 25000',8,lifesnaps['step1goal1label'])

In [42]:
part_df = person_group3.get_group('621e2e8e67b776a24055b564')
grid = setup(data=part_df, target='labels', fold =5,fix_imbalance = True, categorical_features=["id","badgeType","activityType","age","gender","bmi","step_goal","step_goal_label"], html=False, silent=True, verbose=False)
best = compare_models(errors="raise")
print(best)

Model  Accuracy  AUC  Recall  Prec.   F1  Kappa  MCC  \
lr  Logistic Regression       0.0  0.0     0.0    0.0  0.0    0.0  0.0   

    TT (Sec)  
lr     0.002

Model  Accuracy  AUC  Recall  Prec.   F1  Kappa  MCC  \
lr      Logistic Regression       0.0  0.0     0.0    0.0  0.0    0.0  0.0   
knn  K Neighbors Classifier       0.0  0.0     0.0    0.0  0.0    0.0  0.0   

     TT (Sec)  
lr      0.002  
knn     0.004

Model  Accuracy  AUC  Recall  Prec.   F1  Kappa  MCC  \
lr      Logistic Regression       0.0  0.0     0.0    0.0  0.0    0.0  0.0   
knn  K Neighbors Classifier       0.0  0.0     0.0    0.0  0.0    0.0  0.0   
nb              Naive Bayes       0.0  0.0     0.0    0.0  0.0    0.0  0.0   

     TT (Sec)  
lr      0.002  
knn     0.004  
nb      0.004

Model  Accuracy  AUC  Recall  Prec.   F1  Kappa  MCC  \
lr        Logistic Regression       0.0  0.0     0.0    0.0  0.0    0.0  0.0   
knn    K Neighbors Classifier       0.0  0.0     0.0    0.0  0.0    0.0  0.0   
nb                Naive Bayes       0.0  0.0     0.0    0.0  0.0    0.0  0.0   
dt   Decision Tree Classifier       0.0  0.0     0.0    0.0  0.0    0.0  0.0   

     TT (Sec)  
lr      0.002  
knn     0.004  
nb      0.004  
dt      0.004

Model  Accuracy  AUC  Recall  Prec.   F1  Kappa  MCC  \
lr        Logistic Regression       0.0  0.0     0.0    0.0  0.0    0.0  0.0   
knn    K Neighbors Classifier       0.0  0.0     0.0    0.0  0.0    0.0  0.0   
nb                Naive Bayes       0.0  0.0     0.0    0.0  0.0    0.0  0.0   
dt   Decision Tree Classifier       0.0  0.0     0.0    0.0  0.0    0.0  0.0   
svm       SVM - Linear Kernel       0.0  0.0     0.0    0.0  0.0    0.0  0.0   

     TT (Sec)  
lr      0.002  
knn     0.004  
nb      0.004  
dt      0.004  
svm     0.004

...

Model  Accuracy  AUC  Recall  Prec.   F1  \
lr                 Logistic Regression       0.0  0.0     0.0    0.0  0.0   
knn             K Neighbors Classifier       0.0  0.0     0.0    0.0  0.0   
nb                         Naive Bayes       0.0  0.0     0.0    0.0  0.0   
dt            Decision Tree Classifier       0.0  0.0     0.0    0.0  0.0   
svm                SVM - Linear Kernel       0.0  0.0     0.0    0.0  0.0   
ridge                 Ridge Classifier       0.0  0.0     0.0    0.0  0.0   
rf            Random Forest Classifier       0.0  0.0     0.0    0.0  0.0   
qda    Quadratic Discriminant Analysis       0.0  0.0     0.0    0.0  0.0   
ada               Ada Boost Classifier       0.0  0.0     0.0    0.0  0.0   
gbc       Gradient Boosting Classifier       0.0  0.0     0.0    0.0  0.0   
lda       Linear Discriminant Analysis       0.0  0.0     0.0    0.0  0.0   

       Kappa  MCC  TT (Sec)  
lr       0.0  0.0     0.002  
knn      0.0  0.0     0.004  
nb       0.0  0.0     0.004  
dt       0.0  0.0     0.004  
svm      0.0  0.0     0.004  
ridge    0.0  0.0     0.004  
rf       0.0  0.0     0.004  
qda      0.0  0.0     0.004  
ada      0.0  0.0     0.002  
gbc      0.0  0.0     0.004  
lda      0.0  0.0     0.004

Model  Accuracy  AUC  Recall  Prec.   F1  \
lr                 Logistic Regression       0.0  0.0     0.0    0.0  0.0   
knn             K Neighbors Classifier       0.0  0.0     0.0    0.0  0.0   
nb                         Naive Bayes       0.0  0.0     0.0    0.0  0.0   
dt            Decision Tree Classifier       0.0  0.0     0.0    0.0  0.0   
svm                SVM - Linear Kernel       0.0  0.0     0.0    0.0  0.0   
ridge                 Ridge Classifier       0.0  0.0     0.0    0.0  0.0   
rf            Random Forest Classifier       0.0  0.0     0.0    0.0  0.0   
qda    Quadratic Discriminant Analysis       0.0  0.0     0.0    0.0  0.0   
ada               Ada Boost Classifier       0.0  0.0     0.0    0.0  0.0   
gbc       Gradient Boosting Classifier       0.0  0.0     0.0    0.0  0.0   
lda       Linear Discriminant Analysis       0.0  0.0     0.0    0.0  0.0   
et              Extra Trees Classifier       0.0  0.0     0.0    0.0  0.0   

       Kappa  MCC  TT (Sec)  
lr       0.0  0.0     0.002  
knn      0.0  0.0     0.004  
nb       0.0  0.0     0.004  
dt       0.0  0.0     0.004  
svm      0.0  0.0     0.004  
ridge    0.0  0.0     0.004  
rf       0.0  0.0     0.004  
qda      0.0  0.0     0.004  
ada      0.0  0.0     0.002  
gbc      0.0  0.0     0.004  
lda      0.0  0.0     0.004  
et       0.0  0.0     0.002

Model  Accuracy  AUC  Recall  Prec.   F1  \
lr                    Logistic Regression       0.0  0.0     0.0    0.0  0.0   
knn                K Neighbors Classifier       0.0  0.0     0.0    0.0  0.0   
nb                            Naive Bayes       0.0  0.0     0.0    0.0  0.0   
dt               Decision Tree Classifier       0.0  0.0     0.0    0.0  0.0   
svm                   SVM - Linear Kernel       0.0  0.0     0.0    0.0  0.0   
ridge                    Ridge Classifier       0.0  0.0     0.0    0.0  0.0   
rf               Random Forest Classifier       0.0  0.0     0.0    0.0  0.0   
qda       Quadratic Discriminant Analysis       0.0  0.0     0.0    0.0  0.0   
ada                  Ada Boost Classifier       0.0  0.0     0.0    0.0  0.0   
gbc          Gradient Boosting Classifier       0.0  0.0     0.0    0.0  0.0   
lda          Linear Discriminant Analysis       0.0  0.0     0.0    0.0  0.0   
et                 Extra Trees Classifier       0.0  0.0     0.0    0.0  0.0   
lightgbm  Light Gradient Boosting Machine       0.0  0.0     0.0    0.0  0.0   

          Kappa  MCC  TT (Sec)  
lr          0.0  0.0     0.002  
knn         0.0  0.0     0.004  
nb          0.0  0.0     0.004  
dt          0.0  0.0     0.004  
svm         0.0  0.0     0.004  
ridge       0.0  0.0     0.004  
rf          0.0  0.0     0.004  
qda         0.0  0.0     0.004  
ada         0.0  0.0     0.002  
gbc         0.0  0.0     0.004  
lda         0.0  0.0     0.004  
et          0.0  0.0     0.002  
lightgbm    0.0  0.0     0.004

Model  Accuracy  AUC  Recall  Prec.   F1  \
lr                    Logistic Regression       0.0  0.0     0.0    0.0  0.0   
knn                K Neighbors Classifier       0.0  0.0     0.0    0.0  0.0   
nb                            Naive Bayes       0.0  0.0     0.0    0.0  0.0   
dt               Decision Tree Classifier       0.0  0.0     0.0    0.0  0.0   
svm                   SVM - Linear Kernel       0.0  0.0     0.0    0.0  0.0   
ridge                    Ridge Classifier       0.0  0.0     0.0    0.0  0.0   
rf               Random Forest Classifier       0.0  0.0     0.0    0.0  0.0   
qda       Quadratic Discriminant Analysis       0.0  0.0     0.0    0.0  0.0   
ada                  Ada Boost Classifier       0.0  0.0     0.0    0.0  0.0   
gbc          Gradient Boosting Classifier       0.0  0.0     0.0    0.0  0.0   
lda          Linear Discriminant Analysis       0.0  0.0     0.0    0.0  0.0   
et                 Extra Trees Classifier       0.0  0.0     0.0    0.0  0.0   
lightgbm  Light Gradient Boosting Machine       0.0  0.0     0.0    0.0  0.0   
dummy                    Dummy Classifier       0.0  0.0     0.0    0.0  0.0   

          Kappa  MCC  TT (Sec)  
lr          0.0  0.0     0.002  
knn         0.0  0.0     0.004  
nb          0.0  0.0     0.004  
dt          0.0  0.0     0.004  
svm         0.0  0.0     0.004  
ridge       0.0  0.0     0.004  
rf          0.0  0.0     0.004  
qda         0.0  0.0     0.004  
ada         0.0  0.0     0.002  
gbc         0.0  0.0     0.004  
lda         0.0  0.0     0.004  
et          0.0  0.0     0.002  
lightgbm    0.0  0.0     0.004  
dummy       0.0  0.0     0.004

ValueError: Expected n_neighbors <= n_samples,  but n_samples = 1, n_neighbors = 6

In [59]:
accuracies_lifesnaps = []
precision_lifesnaps = []
recall_lifesnaps = []
f1scores_lifesnaps = []


for participant in range(0, 70, 5):
    print("Participant: ",participant)
    part_df = person_group3.get_group(unique_participants3[participant])
    if(participant == 65):
        for part in range(participant+1, participant+6):
            part_df = pd.concat([part_df, person_group3.get_group(unique_participants3[part])])
    
    else:
        for part in range(participant+1, participant+5):
            part_df = pd.concat([part_df, person_group3.get_group(unique_participants3[part])])
    grid = setup(data=part_df, target='labels', fix_imbalance = True, html=False, silent=True, verbose=False)
    best = compare_models(sort='F1')
    accuracies_lifesnaps.append(pull()['Accuracy'][0])
    precision_lifesnaps.append(pull()['Prec.'][0])
    recall_lifesnaps.append(pull()['Recall'][0])
    f1scores_lifesnaps.append(pull()['F1'][0])
    print(best)

Participant:  0


Model  Accuracy     AUC  Recall  Prec.      F1   Kappa  \
lr  Logistic Regression     0.491  0.6157    0.75  0.079  0.1405  0.0496   

       MCC  TT (Sec)  
lr  0.0996     0.007

Model  Accuracy     AUC  Recall   Prec.      F1   Kappa  \
lr      Logistic Regression    0.4910  0.6157    0.75  0.0790  0.1405  0.0496   
knn  K Neighbors Classifier    0.6683  0.6221    0.40  0.0699  0.1183  0.0323   

        MCC  TT (Sec)  
lr   0.0996     0.007  
knn  0.0456     0.011

Model  Accuracy     AUC  Recall   Prec.      F1   Kappa  \
nb              Naive Bayes    0.5587  0.7128    0.85  0.0971  0.1731  0.0858   
lr      Logistic Regression    0.4910  0.6157    0.75  0.0790  0.1405  0.0496   
knn  K Neighbors Classifier    0.6683  0.6221    0.40  0.0699  0.1183  0.0323   

        MCC  TT (Sec)  
nb   0.1776     0.006  
lr   0.0996     0.007  
knn  0.0456     0.011

Model  Accuracy     AUC  Recall   Prec.      F1  \
dt   Decision Tree Classifier    0.9240  0.6762    0.40  0.3250  0.3367   
nb                Naive Bayes    0.5587  0.7128    0.85  0.0971  0.1731   
lr        Logistic Regression    0.4910  0.6157    0.75  0.0790  0.1405   
knn    K Neighbors Classifier    0.6683  0.6221    0.40  0.0699  0.1183   

      Kappa     MCC  TT (Sec)  
dt   0.3011  0.3144     0.014  
nb   0.0858  0.1776     0.006  
lr   0.0496  0.0996     0.007  
knn  0.0323  0.0456     0.011

...

Model  Accuracy     AUC  Recall   Prec.  \
rf            Random Forest Classifier    0.9222  0.9467  0.6000  0.5567   
ada               Ada Boost Classifier    0.9127  0.8886  0.5667  0.5417   
et              Extra Trees Classifier    0.9221  0.9491  0.5917  0.5108   
gbc       Gradient Boosting Classifier    0.9059  0.9260  0.5417  0.5044   
lda       Linear Discriminant Analysis    0.8704  0.8731  0.7000  0.3668   
ridge                 Ridge Classifier    0.8703  0.0000  0.7333  0.3573   
dt            Decision Tree Classifier    0.9059  0.7235  0.5083  0.4433   
nb                         Naive Bayes    0.7642  0.7912  0.7333  0.2128   
knn             K Neighbors Classifier    0.7032  0.7092  0.5833  0.1630   
lr                 Logistic Regression    0.4839  0.7313  0.7417  0.1386   
svm                SVM - Linear Kernel    0.4120  0.0000  0.6000  0.0449   
qda    Quadratic Discriminant Analysis    0.9199  0.4987  0.0000  0.0000   

           F1   Kappa     MCC  TT (Sec)  
rf     0.5453  0.5071  0.5244     0.050  
ada    0.5212  0.4780  0.4951     0.032  
et     0.5202  0.4843  0.5011     0.045  
gbc    0.4847  0.4384  0.4570     0.076  
lda    0.4706  0.4093  0.4413     0.009  
ridge  0.4701  0.4086  0.4484     0.008  
dt     0.4602  0.4122  0.4195     0.014  
nb     0.3280  0.2359  0.3024     0.006  
knn    0.2492  0.1442  0.1832     0.012  
lr     0.2193  0.1023  0.1232     0.007  
svm    0.0834  0.0000  0.0000     0.008  
qda    0.0000 -0.0039 -0.0049     0.007

Model  Accuracy     AUC  Recall   Prec.  \
rf               Random Forest Classifier    0.9222  0.9467  0.6000  0.5567   
ada                  Ada Boost Classifier    0.9127  0.8886  0.5667  0.5417   
et                 Extra Trees Classifier    0.9221  0.9491  0.5917  0.5108   
lightgbm  Light Gradient Boosting Machine    0.9104  0.9312  0.5750  0.5100   
gbc          Gradient Boosting Classifier    0.9059  0.9260  0.5417  0.5044   
lda          Linear Discriminant Analysis    0.8704  0.8731  0.7000  0.3668   
ridge                    Ridge Classifier    0.8703  0.0000  0.7333  0.3573   
dt               Decision Tree Classifier    0.9059  0.7235  0.5083  0.4433   
nb                            Naive Bayes    0.7642  0.7912  0.7333  0.2128   
knn                K Neighbors Classifier    0.7032  0.7092  0.5833  0.1630   
lr                    Logistic Regression    0.4839  0.7313  0.7417  0.1386   
svm                   SVM - Linear Kernel    0.4120  0.0000  0.6000  0.0449   
qda       Quadratic Discriminant Analysis    0.9199  0.4987  0.0000  0.0000   

              F1   Kappa     MCC  TT (Sec)  
rf        0.5453  0.5071  0.5244     0.050  
ada       0.5212  0.4780  0.4951     0.032  
et        0.5202  0.4843  0.5011     0.045  
lightgbm  0.5123  0.4675  0.4833     0.063  
gbc       0.4847  0.4384  0.4570     0.076  
lda       0.4706  0.4093  0.4413     0.009  
ridge     0.4701  0.4086  0.4484     0.008  
dt        0.4602  0.4122  0.4195     0.014  
nb        0.3280  0.2359  0.3024     0.006  
knn       0.2492  0.1442  0.1832     0.012  
lr        0.2193  0.1023  0.1232     0.007  
svm       0.0834  0.0000  0.0000     0.008  
qda       0.0000 -0.0039 -0.0049     0.007

Model  Accuracy     AUC  Recall   Prec.  \
rf               Random Forest Classifier    0.9222  0.9467  0.6000  0.5567   
ada                  Ada Boost Classifier    0.9127  0.8886  0.5667  0.5417   
et                 Extra Trees Classifier    0.9221  0.9491  0.5917  0.5108   
lightgbm  Light Gradient Boosting Machine    0.9104  0.9312  0.5750  0.5100   
gbc          Gradient Boosting Classifier    0.9059  0.9260  0.5417  0.5044   
lda          Linear Discriminant Analysis    0.8704  0.8731  0.7000  0.3668   
ridge                    Ridge Classifier    0.8703  0.0000  0.7333  0.3573   
dt               Decision Tree Classifier    0.9059  0.7235  0.5083  0.4433   
nb                            Naive Bayes    0.7642  0.7912  0.7333  0.2128   
knn                K Neighbors Classifier    0.7032  0.7092  0.5833  0.1630   
lr                    Logistic Regression    0.4839  0.7313  0.7417  0.1386   
svm                   SVM - Linear Kernel    0.4120  0.0000  0.6000  0.0449   
qda       Quadratic Discriminant Analysis    0.9199  0.4987  0.0000  0.0000   
dummy                    Dummy Classifier    0.9223  0.5000  0.0000  0.0000   

              F1   Kappa     MCC  TT (Sec)  
rf        0.5453  0.5071  0.5244     0.050  
ada       0.5212  0.4780  0.4951     0.032  
et        0.5202  0.4843  0.5011     0.045  
lightgbm  0.5123  0.4675  0.4833     0.063  
gbc       0.4847  0.4384  0.4570     0.076  
lda       0.4706  0.4093  0.4413     0.009  
ridge     0.4701  0.4086  0.4484     0.008  
dt        0.4602  0.4122  0.4195     0.014  
nb        0.3280  0.2359  0.3024     0.006  
knn       0.2492  0.1442  0.1832     0.012  
lr        0.2193  0.1023  0.1232     0.007  
svm       0.0834  0.0000  0.0000     0.008  
qda       0.0000 -0.0039 -0.0049     0.007  
dummy     0.0000  0.0000  0.0000     0.004

Model  Accuracy     AUC  Recall   Prec.  \
rf               Random Forest Classifier    0.9222  0.9467  0.6000  0.5567   
ada                  Ada Boost Classifier    0.9127  0.8886  0.5667  0.5417   
et                 Extra Trees Classifier    0.9221  0.9491  0.5917  0.5108   
lightgbm  Light Gradient Boosting Machine    0.9104  0.9312  0.5750  0.5100   
gbc          Gradient Boosting Classifier    0.9059  0.9260  0.5417  0.5044   
lda          Linear Discriminant Analysis    0.8704  0.8731  0.7000  0.3668   
ridge                    Ridge Classifier    0.8703  0.0000  0.7333  0.3573   
dt               Decision Tree Classifier    0.9059  0.7235  0.5083  0.4433   
nb                            Naive Bayes    0.7642  0.7912  0.7333  0.2128   
knn                K Neighbors Classifier    0.7032  0.7092  0.5833  0.1630   
lr                    Logistic Regression    0.4839  0.7313  0.7417  0.1386   
svm                   SVM - Linear Kernel    0.4120  0.0000  0.6000  0.0449   
qda       Quadratic Discriminant Analysis    0.9199  0.4987  0.0000  0.0000   
dummy                    Dummy Classifier    0.9223  0.5000  0.0000  0.0000   

              F1   Kappa     MCC  TT (Sec)  
rf        0.5453  0.5071  0.5244     0.050  
ada       0.5212  0.4780  0.4951     0.032  
et        0.5202  0.4843  0.5011     0.045  
lightgbm  0.5123  0.4675  0.4833     0.063  
gbc       0.4847  0.4384  0.4570     0.076  
lda       0.4706  0.4093  0.4413     0.009  
ridge     0.4701  0.4086  0.4484     0.008  
dt        0.4602  0.4122  0.4195     0.014  
nb        0.3280  0.2359  0.3024     0.006  
knn       0.2492  0.1442  0.1832     0.012  
lr        0.2193  0.1023  0.1232     0.007  
svm       0.0834  0.0000  0.0000     0.008  
qda       0.0000 -0.0039 -0.0049     0.007  
dummy     0.0000  0.0000  0.0000     0.004

RandomForestClassifier(bootstrap=True, ccp_alpha=0.0, class_weight=None,
                       criterion='gini', max_depth=None, max_features='auto',
                       max_leaf_nodes=None, max_samples=None,
                       min_impurity_decrease=0.0, min_impurity_split=None,
                       min_samples_leaf=1, min_samples_split=2,
                       min_weight_fraction_leaf=0.0, n_estimators=100,
                       n_jobs=-1, oob_score=False, random_state=8976, verbose=0,
                       warm_start=False)


In [60]:
mean_acc_lifesnaps = statistics.mean(accuracies_lifesnaps)
mean_prec_lifesnaps = statistics.mean(precision_lifesnaps)
mean_rec_lifesnaps = statistics.mean(recall_lifesnaps)
mean_f1_lifesnaps = statistics.mean(f1scores_lifesnaps)
std_acc_lifesnaps = statistics.stdev(accuracies_lifesnaps)
std_prec_lifesnaps = statistics.stdev(precision_lifesnaps)
std_rec_lifesnaps = statistics.stdev(recall_lifesnaps)
std_f1_lifesnaps = statistics.stdev(f1scores_lifesnaps)

In [61]:
print("Mean Accuracy LifeSnaps: ",mean_acc_lifesnaps)
print("Mean Precision LifeSnaps: ",mean_prec_lifesnaps)
print("Mean Recall LifeSnaps: ",mean_rec_lifesnaps)
print("Mean F1-score LifeSnaps: ",mean_f1_lifesnaps)
print("Standard deviation of Accuracy LifeSnaps: ",std_acc_lifesnaps)
print("Standard deviation of Precision LifeSnaps: ",std_prec_lifesnaps)
print("Standard deviation of Recall LifeSnaps: ",std_rec_lifesnaps)
print("Standard deviation of F1-score LifeSnaps: ",std_f1_lifesnaps)

Mean Accuracy LifeSnaps:  0.9096142857142857
Mean Precision LifeSnaps:  0.6311142857142857
Mean Recall LifeSnaps:  0.6697071428571428
Mean F1-score LifeSnaps:  0.6183142857142857
Standard deviation of Accuracy LifeSnaps:  0.04447389652962143
Standard deviation of Precision LifeSnaps:  0.09367508376660956
Standard deviation of Recall LifeSnaps:  0.14706802959742926
Standard deviation of F1-score LifeSnaps:  0.10099604605469126


## SWELL

In [16]:
swell = pd.read_csv("Final_CSVs/swell.csv")

In [17]:
swell = swell.drop(columns=["Unnamed: 7", "Unnamed: 8", "Unnamed: 9", "Unnamed: 10", "Unnamed: 11", "timestamp", "C"])

In [18]:
swell['Condition'] = np.where(swell['Condition']=='N','No-Stress',swell['Condition'])
swell['Condition'] = np.where(swell['Condition']=='R','No-Stress',swell['Condition'])
swell['Condition'] = np.where(swell['Condition']=='I','Stress',swell['Condition'])
swell['Condition'] = np.where(swell['Condition']=='T','Stress',swell['Condition'])

In [24]:
swell_new['stress'] = np.where(swell_new['stress']=='No-Stress',0,swell_new['stress'])
swell_new['stress'] = np.where(swell_new['stress']=='Stress',1,swell_new['stress'])

In [25]:
swell_new

id stress   HR       RMSSD         SCL
0      PP1      0  999  999.000000   80.239727
1      PP1      0   61    0.061420   77.365127
2      PP1      0   64    0.049663   77.359559
3      PP1      0   60    0.052487   76.728772
4      PP1      0   61    0.051189   76.512877
...    ...    ...  ...         ...         ...
3135  PP25      1  999  999.000000  999.000000
3136  PP25      1  999  999.000000  999.000000
3137  PP25      1  999  999.000000  999.000000
3138  PP25      1  999  999.000000  999.000000
3139  PP25      1  999  999.000000  999.000000

[3140 rows x 5 columns]

In [26]:
#test = swell[swell['dataset']=='Test']

In [10]:
#test.to_csv("Final_CSVs/swell_test.csv", index = False)

In [21]:
swell_new = swell.rename(columns={"PP": "id", "Condition": "stress"})

In [50]:
swell_new

id     stress   HR       RMSSD         SCL
0      PP1  No-Stress  999  999.000000   80.239727
1      PP1  No-Stress   61    0.061420   77.365127
2      PP1  No-Stress   64    0.049663   77.359559
3      PP1  No-Stress   60    0.052487   76.728772
4      PP1  No-Stress   61    0.051189   76.512877
...    ...        ...  ...         ...         ...
3135  PP25     Stress  999  999.000000  999.000000
3136  PP25     Stress  999  999.000000  999.000000
3137  PP25     Stress  999  999.000000  999.000000
3138  PP25     Stress  999  999.000000  999.000000
3139  PP25     Stress  999  999.000000  999.000000

[3140 rows x 5 columns]

In [27]:
X = swell_new[swell_new.columns.difference(['stress'])]
y = swell_new["stress"]

X_train1, X_test, y_train1, y_test = train_test_split(X, y, test_size=0.15, random_state=123)
X_train, X_val, y_train, y_val = train_test_split(X_train1, y_train1, test_size=0.18, random_state=123)

X_train["dataset"] = 'Train'
X_val["dataset"] = 'Val'
X_test["dataset"] = 'Test'

In [28]:
training = pd.concat([X_train, y_train], axis = 1)
validation = pd.concat([X_val, y_val], axis = 1)
test = pd.concat([X_test, y_test], axis = 1)

In [29]:
swell_new = pd.concat([training, validation, test])

In [30]:
swell_new

HR       RMSSD         SCL    id dataset stress
91    999  999.000000   70.787928   PP1   Train      1
1240   61    0.107459  125.057885  PP10   Train      1
2332   78    0.047484  130.011129  PP19   Train      1
11     69    0.052590   67.702527   PP1   Train      0
2579  999  999.000000  294.565800  PP21   Train      1
...   ...         ...         ...   ...     ...    ...
1918   85    0.061362  122.431659  PP16    Test      0
1678  999  999.000000  112.266072  PP14    Test      0
728   999  999.000000  127.856128   PP6    Test      0
1750  999  999.000000  191.407683  PP14    Test      1
387   999  999.000000   77.948910   PP4    Test      0

[3140 rows x 6 columns]

In [31]:
swell_new.to_csv("Final_CSVs/swell_new_new.csv", index = False)

## User-based Models

In [67]:
unique_participants4 = swell["PP"].unique()

In [70]:
len(unique_participants4)

25

In [68]:
person_group4 = swell.groupby('PP')

In [71]:
accuracies_swell = []
precision_swell = []
recall_swell = []
f1scores_swell = []

for participant in unique_participants4:
    print("Participant: ",participant)
    part_df = person_group4.get_group(participant)
    grid = setup(data=part_df, target='Condition', html=False, silent=True, verbose=False) #fix_imbalance = True,
    best = compare_models()
    accuracies_swell.append(pull()['Accuracy'][0])
    precision_swell.append(pull()['Prec.'][0])
    recall_swell.append(pull()['Recall'][0])
    f1scores_swell.append(pull()['F1'][0])
    print(best)

Participant:  PP1


Model  Accuracy    AUC  Recall   Prec.      F1   Kappa  \
lr  Logistic Regression    0.5111  0.555   0.605  0.5237  0.5491 -0.0088   

       MCC  TT (Sec)  
lr -0.0054     0.475

Model  Accuracy    AUC  Recall   Prec.      F1   Kappa  \
knn  K Neighbors Classifier    0.6333  0.670   0.685  0.6679  0.6612  0.2671   
lr      Logistic Regression    0.5111  0.555   0.605  0.5237  0.5491 -0.0088   

        MCC  TT (Sec)  
knn  0.2755     0.269  
lr  -0.0054     0.475

Model  Accuracy     AUC  Recall   Prec.      F1   Kappa  \
knn  K Neighbors Classifier    0.6333  0.6700   0.685  0.6679  0.6612  0.2671   
nb              Naive Bayes    0.5667  0.5775   0.305  0.6917  0.3971  0.1631   
lr      Logistic Regression    0.5111  0.5550   0.605  0.5237  0.5491 -0.0088   

        MCC  TT (Sec)  
knn  0.2755     0.269  
nb   0.1913     0.003  
lr  -0.0054     0.475

Model  Accuracy     AUC  Recall   Prec.      F1  \
dt   Decision Tree Classifier    0.6556  0.6500   0.680  0.6464  0.6558   
knn    K Neighbors Classifier    0.6333  0.6700   0.685  0.6679  0.6612   
nb                Naive Bayes    0.5667  0.5775   0.305  0.6917  0.3971   
lr        Logistic Regression    0.5111  0.5550   0.605  0.5237  0.5491   

      Kappa     MCC  TT (Sec)  
dt   0.3069  0.3154     0.003  
knn  0.2671  0.2755     0.269  
nb   0.1631  0.1913     0.003  
lr  -0.0088 -0.0054     0.475

...

Model  Accuracy     AUC  Recall   Prec.  \
knn             K Neighbors Classifier    0.8875  0.9500   0.910  0.8931   
rf            Random Forest Classifier    0.8653  0.9306   0.915  0.8581   
ada               Ada Boost Classifier    0.8542  0.8781   0.890  0.8481   
et              Extra Trees Classifier    0.8542  0.8981   0.890  0.8481   
dt            Decision Tree Classifier    0.8431  0.8006   0.915  0.8262   
gbc       Gradient Boosting Classifier    0.8319  0.8281   0.890  0.8162   
lr                 Logistic Regression    0.7194  0.9131   0.565  0.9133   
ridge                 Ridge Classifier    0.7069  0.0000   0.540  0.9067   
lda       Linear Discriminant Analysis    0.7069  0.9131   0.540  0.9067   
nb                         Naive Bayes    0.6722  0.6575   1.000  0.6268   
svm                SVM - Linear Kernel    0.5056  0.0000   0.620  0.3867   
qda    Quadratic Discriminant Analysis    0.5056  0.0000   0.800  0.4167   

           F1   Kappa     MCC  TT (Sec)  
knn    0.8925  0.7695  0.7894     0.007  
rf     0.8735  0.7289  0.7536     0.048  
ada    0.8568  0.7047  0.7286     0.015  
et     0.8568  0.7047  0.7286     0.035  
dt     0.8570  0.6815  0.7093     0.003  
gbc    0.8404  0.6574  0.6843     0.010  
lr     0.6454  0.4543  0.5268     0.006  
ridge  0.6321  0.4293  0.4949     0.002  
lda    0.6321  0.4293  0.4949     0.003  
nb     0.7660  0.3274  0.3861     0.004  
svm    0.4673 -0.0265 -0.0398     0.003  
qda    0.5469  0.0000  0.0000     0.003

Model  Accuracy     AUC  Recall   Prec.  \
knn                K Neighbors Classifier    0.8875  0.9500   0.910  0.8931   
rf               Random Forest Classifier    0.8653  0.9306   0.915  0.8581   
ada                  Ada Boost Classifier    0.8542  0.8781   0.890  0.8481   
et                 Extra Trees Classifier    0.8542  0.8981   0.890  0.8481   
dt               Decision Tree Classifier    0.8431  0.8006   0.915  0.8262   
lightgbm  Light Gradient Boosting Machine    0.8417  0.9087   0.940  0.8148   
gbc          Gradient Boosting Classifier    0.8319  0.8281   0.890  0.8162   
lr                    Logistic Regression    0.7194  0.9131   0.565  0.9133   
ridge                    Ridge Classifier    0.7069  0.0000   0.540  0.9067   
lda          Linear Discriminant Analysis    0.7069  0.9131   0.540  0.9067   
nb                            Naive Bayes    0.6722  0.6575   1.000  0.6268   
svm                   SVM - Linear Kernel    0.5056  0.0000   0.620  0.3867   
qda       Quadratic Discriminant Analysis    0.5056  0.0000   0.800  0.4167   

              F1   Kappa     MCC  TT (Sec)  
knn       0.8925  0.7695  0.7894     0.007  
rf        0.8735  0.7289  0.7536     0.048  
ada       0.8568  0.7047  0.7286     0.015  
et        0.8568  0.7047  0.7286     0.035  
dt        0.8570  0.6815  0.7093     0.003  
lightgbm  0.8599  0.6807  0.7162     0.004  
gbc       0.8404  0.6574  0.6843     0.010  
lr        0.6454  0.4543  0.5268     0.006  
ridge     0.6321  0.4293  0.4949     0.002  
lda       0.6321  0.4293  0.4949     0.003  
nb        0.7660  0.3274  0.3861     0.004  
svm       0.4673 -0.0265 -0.0398     0.003  
qda       0.5469  0.0000  0.0000     0.003

Model  Accuracy     AUC  Recall   Prec.  \
knn                K Neighbors Classifier    0.8875  0.9500   0.910  0.8931   
rf               Random Forest Classifier    0.8653  0.9306   0.915  0.8581   
ada                  Ada Boost Classifier    0.8542  0.8781   0.890  0.8481   
et                 Extra Trees Classifier    0.8542  0.8981   0.890  0.8481   
dt               Decision Tree Classifier    0.8431  0.8006   0.915  0.8262   
lightgbm  Light Gradient Boosting Machine    0.8417  0.9087   0.940  0.8148   
gbc          Gradient Boosting Classifier    0.8319  0.8281   0.890  0.8162   
lr                    Logistic Regression    0.7194  0.9131   0.565  0.9133   
ridge                    Ridge Classifier    0.7069  0.0000   0.540  0.9067   
lda          Linear Discriminant Analysis    0.7069  0.9131   0.540  0.9067   
nb                            Naive Bayes    0.6722  0.6575   1.000  0.6268   
dummy                    Dummy Classifier    0.5278  0.5000   1.000  0.5278   
svm                   SVM - Linear Kernel    0.5056  0.0000   0.620  0.3867   
qda       Quadratic Discriminant Analysis    0.5056  0.0000   0.800  0.4167   

              F1   Kappa     MCC  TT (Sec)  
knn       0.8925  0.7695  0.7894     0.007  
rf        0.8735  0.7289  0.7536     0.048  
ada       0.8568  0.7047  0.7286     0.015  
et        0.8568  0.7047  0.7286     0.035  
dt        0.8570  0.6815  0.7093     0.003  
lightgbm  0.8599  0.6807  0.7162     0.004  
gbc       0.8404  0.6574  0.6843     0.010  
lr        0.6454  0.4543  0.5268     0.006  
ridge     0.6321  0.4293  0.4949     0.002  
lda       0.6321  0.4293  0.4949     0.003  
nb        0.7660  0.3274  0.3861     0.004  
dummy     0.6897  0.0000  0.0000     0.003  
svm       0.4673 -0.0265 -0.0398     0.003  
qda       0.5469  0.0000  0.0000     0.003

Model  Accuracy     AUC  Recall   Prec.  \
knn                K Neighbors Classifier    0.8875  0.9500   0.910  0.8931   
rf               Random Forest Classifier    0.8653  0.9306   0.915  0.8581   
ada                  Ada Boost Classifier    0.8542  0.8781   0.890  0.8481   
et                 Extra Trees Classifier    0.8542  0.8981   0.890  0.8481   
dt               Decision Tree Classifier    0.8431  0.8006   0.915  0.8262   
lightgbm  Light Gradient Boosting Machine    0.8417  0.9087   0.940  0.8148   
gbc          Gradient Boosting Classifier    0.8319  0.8281   0.890  0.8162   
lr                    Logistic Regression    0.7194  0.9131   0.565  0.9133   
ridge                    Ridge Classifier    0.7069  0.0000   0.540  0.9067   
lda          Linear Discriminant Analysis    0.7069  0.9131   0.540  0.9067   
nb                            Naive Bayes    0.6722  0.6575   1.000  0.6268   
dummy                    Dummy Classifier    0.5278  0.5000   1.000  0.5278   
svm                   SVM - Linear Kernel    0.5056  0.0000   0.620  0.3867   
qda       Quadratic Discriminant Analysis    0.5056  0.0000   0.800  0.4167   

              F1   Kappa     MCC  TT (Sec)  
knn       0.8925  0.7695  0.7894     0.007  
rf        0.8735  0.7289  0.7536     0.048  
ada       0.8568  0.7047  0.7286     0.015  
et        0.8568  0.7047  0.7286     0.035  
dt        0.8570  0.6815  0.7093     0.003  
lightgbm  0.8599  0.6807  0.7162     0.004  
gbc       0.8404  0.6574  0.6843     0.010  
lr        0.6454  0.4543  0.5268     0.006  
ridge     0.6321  0.4293  0.4949     0.002  
lda       0.6321  0.4293  0.4949     0.003  
nb        0.7660  0.3274  0.3861     0.004  
dummy     0.6897  0.0000  0.0000     0.003  
svm       0.4673 -0.0265 -0.0398     0.003  
qda       0.5469  0.0000  0.0000     0.003

KNeighborsClassifier(algorithm='auto', leaf_size=30, metric='minkowski',
                     metric_params=None, n_jobs=-1, n_neighbors=5, p=2,
                     weights='uniform')


In [72]:
mean_acc_swell = statistics.mean(accuracies_swell)
mean_prec_swell = statistics.mean(precision_swell)
mean_rec_swell = statistics.mean(recall_swell)
mean_f1_swell = statistics.mean(f1scores_swell)
std_acc_swell = statistics.stdev(accuracies_swell)
std_prec_swell = statistics.stdev(precision_swell)
std_rec_swell = statistics.stdev(recall_swell)
std_f1_swell = statistics.stdev(f1scores_swell)

In [73]:
print("Mean Accuracy SWELL: ",mean_acc_swell)
print("Mean Precision SWELL: ",mean_prec_swell)
print("Mean Recall SWELL: ",mean_rec_swell)
print("Mean F1-score SWELL: ",mean_f1_swell)
print("Standard deviation of Accuracy SWELL: ",std_acc_swell)
print("Standard deviation of Precision SWELL: ",std_prec_swell)
print("Standard deviation of Recall SWELL: ",std_rec_swell)
print("Standard deviation of F1-score SWELL: ",std_f1_swell)

Mean Accuracy SWELL:  0.80254
Mean Precision SWELL:  0.815292
Mean Recall SWELL:  0.841736
Mean F1-score SWELL:  0.813352
Standard deviation of Accuracy SWELL:  0.10569543115322756
Standard deviation of Precision SWELL:  0.10554236479569076
Standard deviation of Recall SWELL:  0.12969583288088582
Standard deviation of F1-score SWELL:  0.10986028672818944
